# Run Agent
- Implement a workflow to write a daily AI newsletter
- see README.md for details



```mermaid
  flowchart TD
      Start([Start Newsletter Workflow]) --> Step1[1: Gather URLs<br/>RSS + HTML + REST APIs<br/>17+ sources]

      Step1 --> Step2[2: Filter URLs<br/>Dedupe Previously Seen<br/>LLM AI Filter<br/>]

      Step2 --> Step3[3: Download AI Articles<br/>Extract Text]

      Step3 --> Step4[4: LLM Summarization<br/>Bullet-point summaries]

      Step4 --> Step5[5: Cluster by Topic<br/>HDBSCAN + Embeddings]

      Step5 --> Step6[6: Rate Articles<br/>Identify<br/>On-Topic, Quality<br/>Using Elo 1-1 Comparisons]

      Step6 --> Step7[7: Select Sections<br/>Top Articles by Topic<br/>Newsletter Outline]

      Step7 --> Step8[8: Draft Sections<br/>Write Headlines & Content<br/>Run Critic-Optimizer Loop]

      Step8 --> Critique8[Section Critique<br/>Quality Evaluation]
      Critique8 --> Check8{Score >= 8.0?}
      Check8 -->|No & iter < 3| Improve8[Apply Improvements]
      Improve8 --> Critique8
      Check8 -->|Yes or iter = 3| Step9[9: Finalize Newsletter<br/>Generate Title<br/>Assemble Sections]

      Step9 --> Critique9[Full Newsletter<br/>Critic-Optimizer Loop<br/>Evaluate Quality<br/>5 dimension scores]

      Critique9 --> Check9{Score >= 8.0<br/>OR<br/>iter = 3?}

      Check9 -->|No| Optimizer[Optimizer Agent<br/>Apply Recommendations<br/>Improve Newsletter]
      Optimizer --> Critique9

      Check9 -->|Yes| Final([Publication-Ready<br>Newsletter<br/>Quality Score >= 8.0])

      style Step1 fill:#e1f5ff
      style Step2 fill:#e1f5ff
      style Step3 fill:#e1f5ff
      style Step4 fill:#fff9c4
      style Step5 fill:#fff9c4
      style Step6 fill:#fff9c4
      style Step7 fill:#e8f5e9
      style Step8 fill:#e8f5e9
      style Critique8 fill:#ffe0e0
      style Check8 fill:#ffe0e0
      style Improve8 fill:#ffe0e0
      style Step9 fill:#f3e5f5
      style Critique9 fill:#f3e5f5
      style Check9 fill:#f3e5f5
      style Optimizer fill:#f3e5f5
  ```

In [1]:
import os
import yaml
import dotenv
import logging
import json
import yaml
from datetime import datetime
import time
import random
import glob
import pickle
import sqlite3

from pathlib import Path

import asyncio
import nest_asyncio

import pydantic
from pydantic import BaseModel, Field, RootModel
from typing import Dict, TypedDict, Type, List, Optional, Any, Iterable, Text
from dataclasses import dataclass, field
from enum import Enum

import numpy as np
import pandas as pd

import pandas as pd
from sklearn.metrics import silhouette_score, calinski_harabasz_score, davies_bouldin_score
import hdbscan

import openai
from openai import AsyncOpenAI

import agents
from agents.exceptions import InputGuardrailTripwireTriggered
from agents import (Agent, Runner, Tool, OpenAIResponsesModel, 
                    ModelSettings, FunctionTool, InputGuardrail, GuardrailFunctionOutput,
                    SQLiteSession, set_default_openai_api, set_default_openai_client
                   )


import tenacity
from tenacity import retry, stop_after_attempt, wait_exponential, retry_if_exception_type

from IPython.display import HTML, Image, Markdown, display

from log_handler import SQLiteLogHandler, setup_sqlite_logging, sanitize_error_for_logging
from config import LOGDB
from llm import LLMagent, LangfuseClient  # methods to apply prompts async to large batches
from db import Url, AgentState

from fetch import Fetcher # fetch news urls
from newsletter_state import NewsletterAgentState, StepStatus
from news_agent import NewsletterAgent


In [2]:
print(f"OpenAI:            {openai.__version__}")
print(f"OpenAI Agents SDK  {agents.__version__}")
print(f"Pydantic           {pydantic.__version__}")


OpenAI:            2.6.0
OpenAI Agents SDK  0.4.0
Pydantic           2.12.3


In [3]:
dotenv.load_dotenv()

# to run async in jupyter notebook
nest_asyncio.apply()

# verbose OpenAI console logging if something doesn't work
# logging.basicConfig(level=logging.DEBUG)
# openai_logger = logging.getLogger("openai")
# openai_logger.setLevel(logging.DEBUG)


In [4]:
# modules create a default logger, or we can pass this logger
debuglevel = logging.DEBUG

def setup_logging(session_id: str = "default", db_path: str = "agent_logs.db") -> logging.Logger:
    """Set up logging to console and SQLite database."""

    # Create logger
    logging.basicConfig()
    logger = logging.getLogger(f"NewsletterAgent.{session_id}")
    logger.setLevel(debuglevel)

    # Clear any existing handlers
    logger.handlers.clear()

    # Console handler
    console_handler = logging.StreamHandler()
    console_handler.setLevel(debuglevel)
    console_formatter = logging.Formatter(
        '%(asctime)s | %(name)s | %(levelname)s | %(message)s',
        datefmt='%H:%M:%S'
    )
    console_handler.setFormatter(console_formatter)

    # SQLite handler
    sqlite_handler = SQLiteLogHandler(db_path)
    sqlite_handler.setLevel(debuglevel)
    sqlite_formatter = logging.Formatter('%(message)s')
    sqlite_handler.setFormatter(sqlite_formatter)

    # Add handlers to logger
    logger.addHandler(console_handler)
    logger.addHandler(sqlite_handler)

    # Prevent propagation to root logger
    logger.propagate = False

    return logger

logger = setup_logging("newsletter_agent", "test_logs.db")

# Log some test messages
logger.debug("Test debug message", extra={
    'step_name': 'test_step',
    'agent_session': 'demo_session'
})

logger.info("Test info message", extra={
    'step_name': 'test_step',
    'agent_session': 'demo_session'
})

logger.warning("Test warning message", extra={
    'step_name': 'test_step',
    'agent_session': 'demo_session'
})

logger.error("Test error message", extra={
    'step_name': 'error_step',
    'agent_session': 'demo_session'
})

sanitize_error_for_logging("log with some bad stuff for the filter: sk-proj-123456789012345678901234567890123456789012345678")

09:38:38 | NewsletterAgent.newsletter_agent | DEBUG | Test debug message
09:38:38 | NewsletterAgent.newsletter_agent | INFO | Test info message
09:38:38 | NewsletterAgent.newsletter_agent | WARNING | Test warning message
09:38:38 | NewsletterAgent.newsletter_agent | ERROR | Test error message


'log with some bad stuff for the filter: [API_KEY_REDACTED]'

# Run Agent Worfklow

In [5]:
conn = sqlite3.connect("newsletter_agent.db")
AgentState.list_sessions(conn, n_records=10)


['test_newsletter_20251025072130698561',
 'test_newsletter_20251025073011717872',
 'test_newsletter_20251024180424874055',
 'test_newsletter_20251024084617093238',
 'test_newsletter_20251023183602870404',
 'test_newsletter_20251023074854730516',
 'test_newsletter_20251023182151845889',
 'test_newsletter_20251022174713041313',
 'test_newsletter_20251022074726590734',
 'test_newsletter_20251021183200598515']

In [6]:
z = AgentState.get_latest_by_session(conn, "test_newsletter_20251024180424874055")
z.step_name

'rate_articles'

In [7]:
for y in z.get_all_by_session(conn, "test_newsletter_20251025072130698561"):
    print(y.session_id, y.step_name, y.updated_at)

test_newsletter_20251025072130698561 initialize 2025-10-25 07:21:30.714816
test_newsletter_20251025072130698561 gather_urls 2025-10-25 07:22:11.124031
test_newsletter_20251025072130698561 check_workflow_status 2025-10-25 07:22:12.522015
test_newsletter_20251025072130698561 filter_urls 2025-10-25 07:23:10.199911


In [7]:
print("🚀 Creating NewsletterAgent...")

do_download=False
reprocess_since=None
# reprocess_since='2025-10-23 07:50:58.553139'

try:
    # set up state
    session_id = 'test_newsletter_20251024180424874055'
    step_name = 'rate_articles'
    # del session_id, step_names
except Exception as e:
    print(e)

api_key = os.getenv("OPENAI_API_KEY")
if not api_key:
    raise ValueError("OPENAI_API_KEY environment variable not set")

# Set up OpenAI client for the agents SDK
set_default_openai_client(AsyncOpenAI(api_key=api_key))

# Create agent with persistent state
if 'session_id' in vars():
    # load state from db for session_id and state
    print("session_id is defined")
    print(session_id)
    state = NewsletterAgentState(session_id=session_id, 
                                 db_path="newsletter_agent.db", 
                                 do_download=do_download,
                                 reprocess_since=reprocess_since,
                                 verbose=False
                                )
    state = state.load_from_db(step_name)
    agent = NewsletterAgent(session_id=session_id, state=state, verbose=True, timeout=30)    
else:
    # create new session
    print("session_id is not defined")
    timestamp = datetime.now().strftime("%Y%m%d%H%M%S%f")    
    session_id = f"test_newsletter_{timestamp}"
    print(session_id)
    state = NewsletterAgentState(session_id=session_id, 
                                 db_path="newsletter_agent.db",
                                 do_download=do_download,
                                 reprocess_since=reprocess_since,
                                 verbose=False
                                ) 
    agent = NewsletterAgent(session_id=session_id, state=state, verbose=False, timeout=30)
    state.serialize_to_db("initialize")

09:39:15 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Using provided state with 116 articles


🚀 Creating NewsletterAgent...
session_id is defined
test_newsletter_20251024180424874055
Initialized NewsletterAgent with persistent state and 9-step workflow
Session ID: test_newsletter_20251024180424874055


In [28]:
agent.state.get_status()


{'headlines': {'total': 183},
 'sources': {'config_file': 'sources.yaml', 'loaded_sources': 0},
 'topics': {'cluster_topics': 0, 'topics': []},
 'workflow': {'current_step': 'cluster_topics',
  'workflow_complete': False,
  'progress_percentage': 55.55555555555556,
  'completed_steps': 5,
  'total_steps': 9,
  'max_edits': 2,
  'concurrency': 16,
  'do_download': True,
  'reprocess_since': None},
 'processing': {'topic_clusters': 0,
  'newsletter_sections': 0,
  'final_newsletter_length': 0}}

In [27]:
state.complete_step('rate_articles')

In [21]:
state.headline_df_to_dict(ydf)

In [29]:
state.headline_df.sort_values("rating")


source                                              title  \
66     NewsAPI  EU says it won't 'lecture' Canada as it moves ...   
65   Feedly AI  These are my favorite ChatGPT prompts after a ...   
64     NewsAPI  New Marriott Bonvoy Research reveals importanc...   
182  Feedly AI  This AI tool could speed up one of the most aw...   
173    NewsAPI  Alberta Seeks to Use Gas Reserves to Become AI...   
..         ...                                                ...   
67          FT  Nuclear treaties offer a blueprint for how to ...   
116    NewsAPI  Anthropic to use Google's AI chips worth tens ...   
16   Feedly AI  Google, Anthropic Announce Cloud Deal Worth Te...   
131  Feedly AI  Google Earth AI: Unlocking geospatial insights...   
169    NewsAPI  Anthropic Announces Massive AI Chip Deal With ...   

                                                   url             published  \
66   https://www.nationalobserver.com/2025/10/24/ne...  2025-10-24T11:09:16Z   
65   https://www.digitaltrends.com/computing/these-...                  None   
64    https://www.hospitalitynet.org/news/4129472.html  2025-10-24T08:42:48Z   
182  https://www.creativebloq.com/3d/this-ai-tool-c...                  None   
173  https://financialpost.com/pmn/business-pmn/alb...  2025-10-23T20:49:45Z   
..                                                 ...                   ...   
67   https://www.ft.com/content/767d1feb-2c6a-4385-...                  None   
116  https://finance.yahoo.com/news/anthropic-googl...  2025-10-23T21:28:29Z   
16   https://finance.yahoo.com/news/google-anthropi...                  None   
131  https://news.google.com/rss/articles/CBMiwgFBV...                  None   
169  https://www.ibtimes.com/anthropic-announces-ma...  2025-10-23T21:57:05Z   

    rss_summary   id  isAI  status  \
66         None   66  True     520   
65         None   65  True  exists   
64         None   64  True     200   
182        None  182  True     200   
173        None  173  True  exists   
..          ...  ...   ...     ...   
67         None   67  True     200   
116        None  116  True     200   
16         None   16  True  exists   
131        None  131  True     200   
169        None  169  True     200   

                                             final_url  \
66   https://www.nationalobserver.com/2025/10/24/ne...   
65   https://www.digitaltrends.com/computing/these-...   
64    https://www.hospitalitynet.org/news/4129472.html   
182  https://www.creativebloq.com/3d/this-ai-tool-c...   
173  https://financialpost.com/pmn/business-pmn/alb...   
..                                                 ...   
67   https://www.ft.com/content/767d1feb-2c6a-4385-...   
116  https://finance.yahoo.com/news/anthropic-googl...   
16   https://finance.yahoo.com/news/google-anthropi...   
131  https://research.google/blog/google-earth-ai-u...   
169  https://www.ibtimes.com/anthropic-announces-ma...   

                                             html_path  ...  \
66                                                      ...   
65   download/html/These_are_my_favorite_ChatGPT_pr...  ...   
64   download/html/New_Marriott_Bonvoy_Research_rev...  ...   
182  download/html/This_AI_tool_could_speed_up_one_...  ...   
173  download/html/Alberta_Seeks_to_Use_Gas_Reserve...  ...   
..                                                 ...  ...   
67   download/html/Nuclear_treaties_offer_a_bluepri...  ...   
116  download/html/Anthropic_to_use_Google_s_AI_chi...  ...   
16   download/html/Google__Anthropic_Announce_Cloud...  ...   
131  download/html/Google_Earth_AI__Unlocking_geosp...  ...   
169  download/html/Anthropic_Announces_Massive_AI_C...  ...   

                                            input_text       age  \
66   EU says it won't 'lecture' Canada as it moves ...  1.000007   
65   These are my favorite ChatGPT prompts after a ...  1.000007   
64   New Marriott Bonvoy Research reveals importanc...  1.125968   
182  This AI tool could speed up on

In [18]:
ydf = pd.concat((zdf, xdf))
ydf = ydf.reset_index(drop=True)


In [19]:
ydf["id"]=ydf.index
ydf


source                                              title  \
0        Techmeme  Grab is investing an undisclosed amount in May...   
1    The Register  Berkeley boffins build better load balancing a...   
2       Feedly AI  Gear News of the Week: There’s Yet Another New...   
3       Feedly AI  Sam Altman’s next startup eyes using sound wav...   
4       Feedly AI  OpenAI's Atlas Wants to Be the Web’s Tour Guid...   
..            ...                                                ...   
178       NewsAPI  Apple begins shipping American-made AI servers...   
179       NewsAPI  Meta replacing humans with AI for FTC-mandated...   
180     Feedly AI  What Is One of the BestArtificial Intelligence...   
181       NewsAPI  OpenAI buys AI startup that built interface fo...   
182     Feedly AI  This AI tool could speed up one of the most aw...   

                                                   url  \
0    https://www.bloomberg.com/news/articles/2025-1...   
1    https://go.theregister.com/feed/www.theregiste...   
2    https://www.wired.com/story/gear-news-of-the-w...   
3    https://www.theverge.com/column/806666/sam-alt...   
4    https://www.wired.com/story/web-browsers-ai-to...   
..                                                 ...   
178              https://biztoc.com/x/75009b6579fe8474   
179              https://biztoc.com/x/2dc8a08f38b3234e   
180  https://finance.yahoo.com/news/one-best-artifi...   
181              https://biztoc.com/x/e64c8f801763ca74   
182  https://www.creativebloq.com/3d/this-ai-tool-c...   

                   published  \
0                       None   
1    2025-10-25T00:00:24.00Z   
2                       None   
3                       None   
4                       None   
..                       ...   
178     2025-10-23T21:29:24Z   
179     2025-10-23T20:33:57Z   
180                     None   
181     2025-10-23T18:32:21Z   
182                     None   

                                           rss_summary   id  isAI   status  \
0                                                 None    0  True  skipped   
1    <h4>One way AI can improve on human work</h4> ...    1  True      200   
2                                                 None    2  True      200   
3                                                 None    3  True      200   
4                                                 None    4  True      200   
..                                                 ...  ...   ...      ...   
178                                               None  178  True      200   
179                                               None  179  True      200   
180                                               None  180  True      200   
181                                               None  181  True      200   
182                                               None  182  True      200   

                                             final_url  \
0    https://www.bloomberg.com/news/articles/2025-1...   
1    https://www.theregister.com/2025/10/25/openevo...   
2    https://www.wired.com/story/gear-news-of-the-w...   
3    https://www.theverge.com/column/806666/sam-alt...   
4    https://www.wired.com/story/web-browsers-ai-to...   
..                                                 ...   
178              https://biztoc.com/x/75009b6579fe8474   
179              https://biztoc.com/x/2dc8a08f38b3234e   
180  https://www.fool.com/investing/2025/10/23/what...   
181              https://biztoc.com/x/e64c8f801763ca74   
182  https://www.creativebloq.com/3d/this-ai-tool-c...   

                                             html_path  ...  \
0                                                       ...   
1    download/html/Berkeley_boffins_build_better_lo...  ...   
2    download/html/Gear_News_of_the_Week__There_s_Y...  ...   
3    download/html/Sam_Altman_s_next_startup_eyes_u...  ...   
4    download/html/OpenAI_s_Atlas_Wants_to_Be_the_W...  ...   
..                                                 .

In [8]:
for step in agent.state.steps:
    print(step)
    print("---")


✅ Gather URLs [complete] (took 33.5s)
   ✅ Step 1 gather_urls completed successfully! Gathered 858 articles from 17 sources.

📊 Articles stored in persistent state: 740
---
✅ Filter URLs [complete] (took 53.5s)
   ✅ Step 2 filter_urls completed successfully! Removed 559 duplicate URLs, classified 181 new articles, found 72 AI-related.
---
⚪ Download Articles [not_started]
   
---
⚪ Extract Summaries [not_started]
   
---
⚪ Rate Articles [not_started]
   
---
⚪ Cluster By Topic [not_started]
   
---
⚪ Select Sections [not_started]
   
---
⚪ Draft Sections [not_started]
   
---
⚪ Finalize Newsletter [not_started]
   
---


In [13]:
# User prompt to run workflow
user_prompt = "Show the workflow status"

print(f"\n📝 User prompt: '{user_prompt}'")
print("=" * 80)

# Run the agent with persistent state
start_time = time.time()
result = await agent.run_step(user_prompt)
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


📝 User prompt: 'Show the workflow status'


18:04:30 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Starting check_workflow_status
18:04:30 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Completed check_workflow_status


⏱️  Total execution time: 7.07s
📊 Final result:
Current workflow status:

- Progress: 0.0% (0/9 complete)
- Status: 0 complete, 0 started, 0 failed, 9 not started
- Next step: Step 0 — Gather URLs

Step-by-step:
- Step 0: Gather URLs — not_started
- Step 1: Filter URLs — not_started
- Step 2: Download Articles — not_started
- Step 3: Extract Summaries — not_started
- Step 4: Rate Articles — not_started
- Step 5: Cluster By Topic — not_started
- Step 6: Select Sections — not_started
- Step 7: Draft Sections — not_started
- Step 8: Finalize Newsletter — not_started

What would you like me to do next? (I can start the workflow, run a specific step, or inspect detailed state.)


In [14]:
# User prompt to run a workflow step
user_prompt = "Run step 1, fetch urls"

print(f"\n📝 User prompt: '{user_prompt}'")
print("=" * 80)

# Run the agent with persistent state
start_time = time.time()
result = await agent.run_step(user_prompt)
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)



📝 User prompt: 'Run step 1, fetch urls'


18:04:39 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Starting check_workflow_status
18:04:39 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Completed check_workflow_status
18:04:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Starting Step 1: Gather URLs
18:04:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Cleaning out download/sources: 
18:04:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully cleaned out download/sources
18:04:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Cleaning out download/text: 
18:04:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully cleaned out download/text
18:04:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Cleaning out download/html: 
18:04:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully cleaned out download/html
2025-10-24 18:04:41,592 - fetcher_5671029

▶ Starting Step 1: gather_urls


2025-10-24 18:04:41,767 - fetcher_5671029328 - INFO - [fetch_rss] RSS fetch successful for New York Times: 25 articles
2025-10-24 18:04:41,767 - fetcher_5671029328 - INFO - [fetch_html] Fetching HTML from Reddit: https://www.reddit.com/r/AI_Agents+ArtificialInteligence+Automate+ChatGPT+ChatGPTCoding+Futurology+MachineLearning+OpenAI+ProgrammerHumor+accelerate+aiArt+aivideo+artificial+deeplearning+learnmachinelearning+programming+singularity+tech+technews+technology/top/?sort=top&t=day
2025-10-24 18:04:41,868 - fetcher_5671029328 - INFO - [fetch_rss] RSS fetch successful for HackerNoon: 50 articles
2025-10-24 18:04:41,869 - fetcher_5671029328 - INFO - [fetch_html] Fetching HTML from Techmeme: https://www.techmeme.com/river
2025-10-24 18:04:41,950 - fetcher_5671029328 - INFO - [fetch_rss] RSS fetch successful for Ars Technica: 20 articles
2025-10-24 18:04:41,951 - fetcher_5671029328 - INFO - [fetch_rss] Fetching RSS from The Register: https://www.theregister.com/software/ai_ml/headlines.

source  url
0       Ars Technica   20
1          Bloomberg   28
2   Business Insider   16
3                 FT   55
4          Feedly AI   99
5        Hacker News   30
6         HackerNoon   50
7     New York Times   25
8            NewsAPI   93
9             Reddit   45
10          Techmeme  198
11      The Guardian   23
12      The Register   50
13         The Verge   29
14       VentureBeat   12
15               WSJ   17
16   Washington Post   20

source                                              title  \
0    Ars Technica  Microsoft’s Mico heightens the risks of paraso...   
1    Ars Technica  With new acquisition, OpenAI signals plans to ...   
2    Ars Technica  Lawsuit: Reddit caught Perplexity “red-handed”...   
3    Ars Technica  Researchers show that training on “junk data” ...   
4    Ars Technica  We let OpenAI’s “Agent Mode” surf the web for ...   
..            ...                                                ...   
805       NewsAPI  Capita rubbishes Public Accounts Committee rep...   
806       NewsAPI  Elon Musk defends pay package as Tesla profits...   
807       NewsAPI  After OpenAI’s new ‘buy it in ChatGPT’ trial, ...   
808       NewsAPI  Putin decries U.S. sanctions as ‘unfriendly’ a...   
809       NewsAPI  Meta replacing humans with AI for FTC-mandated...   

                                                   url  \
0    https://arstechnica.com/ai/2025/10/microsofts-...   
1    https://arstechnica.com/ai/2025/10/openai-acqu...   
2    https://arstechnica.com/tech-policy/2025/10/re...   
3    https://arstechnica.com/ai/2025/10/researchers...   
4    https://arstechnica.com/features/2025/10/we-le...   
..                                                 ...   
805  https://www.computerweekly.com/news/366633358/...   
806  https://rollingout.com/2025/10/23/musk-pay-pac...   
807  https://theconversation.com/after-openais-new-...   
808  https://www.pbs.org/newshour/world/putin-decri...   
809  https://www.cnbc.com/2025/10/23/meta-replacing...   

                           published  \
0    Fri, 24 Oct 2025 17:07:57 +0000   
1    Thu, 23 Oct 2025 22:08:40 +0000   
2    Thu, 23 Oct 2025 21:54:39 +0000   
3    Thu, 23 Oct 2025 21:20:48 +0000   
4    Thu, 23 Oct 2025 11:00:08 +0000   
..                               ...   
805             2025-10-23T19:01:00Z   
806             2025-10-23T19:29:15Z   
807             2025-10-23T19:09:14Z   
808             2025-10-23T19:32:25Z   
809             2025-10-23T20:29:26Z   

                                           rss_summary   id  
0    "It looks like you're trying to find a friend....    0  
1    The acquired firm was working on a tool to con...    1  
2    Scraper accused of stealing Reddit content "sh...    2  
3    Models trained on short, popular, and/or "supe...    3  
4    From scanning emails to building fansites, Atl...    4  
..                                                 ...  ...  
805                                                NaN  805  
806                                                NaN  806  
807                                                NaN  807  
808                                                NaN  808  
809                                                NaN  809  

[810 rows x 6 columns]

18:05:17 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Completed Step 1: Gathered 925 articles
18:05:22 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Starting check_workflow_status
18:05:22 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Completed check_workflow_status


⏱️  Total execution time: 50.87s
📊 Final result:
Step 1 (Gather URLs) has been run.

Summary:
- Result: Completed successfully
- Collected: 925 headlines/URLs from 17 sources
- Articles stored in persistent state: 810
- Workflow progress: 11.1% (1/9 steps complete)
- Next step: Step 1 — Filter URLs

Would you like me to run the next step (filter URLs) now?


In [15]:
countdf = pd.DataFrame(state.headline_data) \
    .groupby("source") \
    .count()[["id"]] \
    .reset_index() \
    .rename(columns={'id': 'count'}) \
    .sort_values("count", ascending=False)
countdf 


source  count
10          Techmeme    198
4          Feedly AI     99
8            NewsAPI     93
3                 FT     55
12      The Register     50
6         HackerNoon     50
9             Reddit     45
5        Hacker News     30
13         The Verge     29
1          Bloomberg     28
7     New York Times     25
11      The Guardian     23
0       Ars Technica     20
16   Washington Post     20
15               WSJ     17
2   Business Insider     16
14       VentureBeat     12

In [10]:
# Run tool directly without LLM processing an input prompt or results
# user_prompt = "Run step 2, filter urls"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

# Run the agent with persistent state
start_time = time.time()
result = await agent.run_tool_direct("filter_urls")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


07:27:12 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Starting Step 2: Filter URLs


⏱️  Total execution time: 0.01s
📊 Final result:
Step 2 already completed! Filtered 181 articles, 72 identified as AI-related.


In [9]:
# User prompt to run workflow
# user_prompt = "Run step 3, download full articles"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

# Run the agent with persistent state
start_time = time.time()
result = await agent.run_tool_direct("download_articles")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


07:39:25 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Starting Step 3: Download Articles
07:39:25 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Starting concurrent scraping of 72 AI-related articles


▶ Starting Step 3: download_articles


07:39:25 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Launching browser for 72 URLs with 16 concurrent workers
07:39:26 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Worker 0 fetching 1 of 72 https://go.theregister.com/feed/www.theregister.com/2025/10/25/openevolve_ai_better_algorithms/
07:39:26 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | scrape_url(https://go.theregister.com/feed/www.theregister.com/2025/10/25/openevolve_ai_better_algorithms/)
07:39:26 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | scraping https://go.theregister.com/feed/www.theregister.com/2025/10/25/openevolve_ai_better_algorithms/ to download/html
07:39:26 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Downloading https://go.theregister.com/feed/www.theregister.com/2025/10/25/openevolve_ai_better_algorithms/
07:39:26 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Worker 1 fetching 2 of 72 https://sherwood.ne

Starting with 71 rows...
Processing 71 files...
Reading and truncating files to 8192 tokens using text-embedding-3-large tokenizer...
Error reading : [Errno 2] No such file or directory: ''
Error reading : [Errno 2] No such file or directory: ''
Error reading : [Errno 2] No such file or directory: ''
Error reading : [Errno 2] No such file or directory: ''
Error reading : [Errno 2] No such file or directory: ''
Error reading : [Errno 2] No such file or directory: ''
Getting embeddings for 65 texts...
Creating indexed similarity matrix...
Finding pairs with similarity > 0.925...
Filtering dataframe...
  Pair: 61 vs 63
    61: NewsAPI - Profound Named to Redpoint Ventures’ Inaugural AI64 List of the Most Promising AI Companies Shaping the Future
    61: https://www.globenewswire.com/news-release/2025/10/24/3172679/0/en/Profound-Named-to-Redpoint-Ventures-Inaugural-AI64-List-of-the-Most-Promising-AI-Companies-Shaping-the-Future.html
    63: NewsAPI - Profound Named to Redpoint Ventures’ In

title  \
21                                                                Baltimore County school’s use of AI security system under scrutiny after student’s bag of chips was mistaken for a gun   
12                                                                                                                                          It's getting harder to take OpenAI seriously   
45                          Oreo maker Mondelez has spent $40M+ on an AI tool, developed with Publicis and Accenture, to cut costs for the production of marketing content by 30% to 50%   
64                                                                                            EU says it won't 'lecture' Canada as it moves ahead with tech, AI regulation: commissioner   
44                              Grab is investing an undisclosed amount in May Mobility as part of a multiyear deal, which includes bringing robotaxis to Southeast Asia as soon as 2026   
41  Shares of Japanese optical fiber maker Fujikura are up ~171% YTD, outpacing the Nikkei's 22% and lifting its market cap to $33B+ amid the AI data center boom (Junko Fujita/Reuters)   

     status  \
21  skipped   
12      403   
45      401   
64      520   
44  skipped   
41      401   

                                                                                                                              final_url  
21                                                       https://www.cnn.com/2025/10/25/us/baltimore-student-chips-ai-gun-detection-hnk  
12                                                     https://www.fastcompany.com/91428080/its-getting-harder-to-take-openai-seriously  
45      https://www.reuters.com/business/media-telecom/oreo-maker-mondelez-use-new-generative-ai-tool-slash-marketing-costs-2025-10-24/  
64       https://www.nationalobserver.com/2025/10/24/news/eu-says-it-wont-lecture-canada-it-moves-ahead-tech-ai-regulation-commissioner  
44      https://www.bloomberg.com/news/articles/2025-10-23/singapore-s-grab-backs-may-mobility-ahead-of-robotaxi-launch-as-soon-as-2026  
41  https://www.reuters.com/world/asia-pacific/japans-century-old-fujikura-rides-ai-data-centre-boom-become-nikkei-standout-2025-10-24/

07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Completed Step 3: Downloaded 66 articles


✅ Completed Step 3: Downloaded 66 AI-related articles
⏱️  Total execution time: 215.93s
📊 Final result:
✅ Step 3 download_articles completed successfully! Downloaded 66 AI-related articles with 96% success rate.
📊 Average article length: 5681 characters
🔗 Content stored in persistent state.


In [10]:
headline_df = state.headline_df
with pd.option_context('display.max_columns', None, 'display.width', None, 'display.max_colwidth', None  ):
    display(headline_df[['id', 'source', 'title', 'status', 'final_url']].loc[headline_df["status"]!=200])




id            source  \
2   150         Feedly AI   
3   732           NewsAPI   
4   137         Feedly AI   
5   678           NewsAPI   
10  683           NewsAPI   
12  709           NewsAPI   
13  125         Feedly AI   
15  170         Feedly AI   
23  734           NewsAPI   
27  684           NewsAPI   
28  157         Feedly AI   
39  713           NewsAPI   
40  735           NewsAPI   
44  127         Feedly AI   
46  177         Feedly AI   
51   52  Business Insider   
53  692           NewsAPI   
55    0      Ars Technica   
56  173         Feedly AI   
57   57  Business Insider   
59  722           NewsAPI   
61  317            Reddit   
62  697           NewsAPI   
63  145         Feedly AI   
64  129         Feedly AI   
65  334          Techmeme   
66  721           NewsAPI   
67  331          Techmeme   
68  178         Feedly AI   

                                                                                                                                                                                    title  \
2                 A look at AI startups aiming to address loneliness among the elderly; a study predicts the AI market for aging and elderly care will grow to over $43B in 2025 (Forbes)   
3   United States Precision Medicine Market Analysis Report 2025-2033: Developments in Biomarker Identification and Genomic Sequencing, & Combining Big Data Analytics and AI Fuel Growth   
4                                                                                                                         Homework faces an existential crisis. Has AI made it pointless?   
5                                                                                                         AI Miners Surge Pre-Market on Record $38B Oracle Data Center Deal Boosts Sector   
10                                                                                                     Discover the Secret Behind Claude Skills : Benefits of Modular Scalable AI Systems   
12                                                                                                                ICAI to arm CAs with AI tools for sharper audits: Charanjot Singh Nanda   
13                                                                                                                  Google TPUs Find Sweet Spot of AI Demand, a Decade After Chip’s Debut   
15                                                                      CoreWeave Is 'Frightening... It's Unbelievable,' Says Expert, Expecting Its Revenue To Multiply Nearly 5x By 2028   
23                                                                                                                                     Nvidia partnership sends Uber shares climbing high   
27                                                                                                      How to Use AI Chatbots and What to Know About These Artificial Intelligence Tools   
28                                                                                                           These are my favorite ChatGPT prompts after a year of using OpenAI’s chatbot   
39                                                                         Profound Named to Redpoint Ventures’ Inaugural AI64 List of the Most Promising AI Companies Shaping the Future   
40                                                                                         Federal judges acknowledge court ruling errors tied to staffers’ AI use after Grassley inquiry   
44                                                                                                    Sam Altman Now Has the Power to “Crash the Global Economy,” Financial Analyst Warns   
46                                                                                                                           Google, Anthropic Announce Cloud Deal Worth Tens of Billions   
51                                                                                                            

In [11]:
headline_df = state.headline_df
with pd.option_context('display.max_columns', None, 'display.width', None, 'display.max_colwidth', None  ):
    display(headline_df[['id', 'source', 'title', 'status', 'final_url']].loc[headline_df["html_path"]==""])



id     source  \
63  145  Feedly AI   
64  129  Feedly AI   
65  334   Techmeme   
66  721    NewsAPI   
67  331   Techmeme   
68  178  Feedly AI   

                                                                                                                                                                                   title  \
63                                                                Baltimore County school’s use of AI security system under scrutiny after student’s bag of chips was mistaken for a gun   
64                                                                                                                                          It's getting harder to take OpenAI seriously   
65                          Oreo maker Mondelez has spent $40M+ on an AI tool, developed with Publicis and Accenture, to cut costs for the production of marketing content by 30% to 50%   
66                                                                                            EU says it won't 'lecture' Canada as it moves ahead with tech, AI regulation: commissioner   
67                              Grab is investing an undisclosed amount in May Mobility as part of a multiyear deal, which includes bringing robotaxis to Southeast Asia as soon as 2026   
68  Shares of Japanese optical fiber maker Fujikura are up ~171% YTD, outpacing the Nikkei's 22% and lifting its market cap to $33B+ amid the AI data center boom (Junko Fujita/Reuters)   

     status  \
63  skipped   
64      403   
65      401   
66      520   
67  skipped   
68      401   

                                                                                                                              final_url  
63                                                       https://www.cnn.com/2025/10/25/us/baltimore-student-chips-ai-gun-detection-hnk  
64                                                     https://www.fastcompany.com/91428080/its-getting-harder-to-take-openai-seriously  
65      https://www.reuters.com/business/media-telecom/oreo-maker-mondelez-use-new-generative-ai-tool-slash-marketing-costs-2025-10-24/  
66       https://www.nationalobserver.com/2025/10/24/news/eu-says-it-wont-lecture-canada-it-moves-ahead-tech-ai-regulation-commissioner  
67      https://www.bloomberg.com/news/articles/2025-10-23/singapore-s-grab-backs-may-mobility-ahead-of-robotaxi-launch-as-soon-as-2026  
68  https://www.reuters.com/world/asia-pacific/japans-century-old-fujikura-rides-ai-data-centre-boom-become-nikkei-standout-2025-10-24/

In [12]:
# User prompt to run workflow
# user_prompt = "Run step 4, Summarize articles"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

start_time = time.time()
result = await agent.run_tool_direct("extract_summaries")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)

07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Processing 69 AI articles for summarization
07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Initialized LangfuseClient
07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Successfully retrieved prompt 'newsagent/extract_summaries' from Langfuse
07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Parsed prompt 'newsagent/extract_summaries': model=gpt-5-mini, reasoning_effort=medium, system_len=1273, user_len=43
07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Using model 'gpt-5-mini' for summarization


▶ Starting Step 4: extract_summaries


07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Initialized with Langfuse tracing enabled (tags: ['extract_summaries', 'summary_agent'])
07:43:01 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Initialized LLMagent:
system_prompt: You are an expert AI news analyst. Your task is to create concise, informative bullet-point summaries of AI and technology articles for a professional newsletter audience.

You will receive a list of JSON object with fields "id" and "title"
Return **only** a JSON object that satisfies the provided schema.
For each article provided, you MUST return one element with the same id, and the summary.
Return elements in the same order they were provided.
No markdown, no markdown fences, no extra keys, no comments.

Write a summary with 3 bullet points (-) that capture ONLY the newsworthy content.

Include
- Key facts & technological developments
- Business implications and market impact
- Future outlook and expert predictions


✅ Completed Step 4: Generated AI summaries for 69/69 articles
⏱️  Total execution time: 70.45s
📊 Final result:
✅ Step 4 extract_summaries completed successfully! Generated AI-powered summaries for 69/69 articles.
💾 Summaries stored in headline DataFrame.


In [19]:
# if we get a refusal, examine why and delete bad rows
bad_stuff =["Anthropic's Jack Cla",
           ]
print([len(s) for s in bad_stuff])
headline_df = state.headline_df
headline_df.loc[(headline_df["title"].str[:20].isin(bad_stuff))]



[20]


Empty DataFrame
Columns: [source, title, url, published, rss_summary, id, isAI, status, final_url, html_path, last_updated, text_path, content_length, domain, site_name, reputation, summary, description, tags, short_summary]
Index: []

In [20]:
# remove bad stuff
state.headline_df_to_dict(headline_df.loc[~headline_df["title"].str[:20].isin(bad_stuff)])


In [13]:
# User prompt to run workflow
# user_prompt = "Run step 5, Rate articles"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

start_time = time.time()
result = await agent.run_tool_direct("rate_articles")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


07:44:11 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Rating 69 AI articles using fn_rate_articles
07:44:11 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Calculating article ratings for 69 articles
07:44:11 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Rating recency
07:44:11 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Rating spam probability
07:44:11 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Successfully retrieved prompt 'newsagent/rate_quality' from Langfuse
07:44:11 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Parsed prompt 'newsagent/rate_quality': model=gpt-4.1, reasoning_effort=medium, system_len=1849, user_len=246


▶ Starting Step 5: rate_articles


07:44:18 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | low quality articles: {0.0: 57, 1.0: 2, 6.47594599989589e-07: 1, 0.43782350042481233: 1, 8.592166619174109e-10: 1, 0.029312225847906822: 1, 4.1937956583795446e-13: 1, 0.0019267342527389902: 1, 2.9989608248573072e-09: 1, 0.9996199233400158: 1, 0.00020342704214340812: 1, 0.4073333999755006: 1}
07:44:18 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Successfully retrieved prompt 'newsagent/rate_on_topic' from Langfuse
07:44:18 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Parsed prompt 'newsagent/rate_on_topic': model=gpt-4.1, reasoning_effort=medium, system_len=1790, user_len=240
07:44:20 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | on topic articles: {1.0: 58, 0.0: 2, 0.008577484930474293: 1, 0.9999756083407958: 1, 0.5621765025686553: 1, 0.9999998063873693: 1, 6.47594599989589e-07: 1, 0.9997964803243284: 1, 0.9999784691634502: 1, 0.6224593113235651: 1, 0.9999965

id         site_name  \
16  16             Yahoo   
31  31       VentureBeat   
54  54     Sherwood News   
3    3         The Verge   
44  44   Computer Weekly   
..  ..               ...   
39  39         Live Mint   
65  65      Fast Company   
6    6  Business Insider   
47  47   The Motley Fool   
23  23  Business Insider   

                                                                                                                                       title  \
16                                                                              Google, Anthropic Announce Cloud Deal Worth Tens of Billions   
31                        OpenAI launches company knowledge in ChatGPT, letting you access your firm's data from Google Drive, Slack, GitHub   
54                   Data center and AI energy stocks rise as Trump administration reportedly pushes for data centers to access power faster   
3                                                                        Sam Altman’s next startup eyes using sound waves to read your brain   
44                                                                          Banks’ AI cost-cutting benefits won’t last, will ‘erode’ profits   
..                                                                                                                                       ...   
39                                                                   ICAI to arm CAs with AI tools for sharper audits: Charanjot Singh Nanda   
65                                                                                              It's getting harder to take OpenAI seriously   
6                                          I designed a custom GPT that helped me land 7 interviews and a job offer from PayPal — here's how   
47                                               1 SpectacularArtificial Intelligence(AI) Stock Down 42% You'll Regret Not Buying on the Dip   
23  A legendary economist says Gen Z will have to 'work a lot harder' to survive the AI era &mdash; and may end up poorer than their parents   

    bradley_terry      bt_z  
16      24.091954  1.496258  
31      24.091954  1.496258  
54      24.091954  1.496258  
3       24.091954  1.496258  
44      24.091954  1.496258  
..            ...       ...  
39     -24.091954 -1.496258  
65     -24.091954 -1.496258  
6      -24.091954 -1.496258  
47     -24.091954 -1.496258  
23     -24.091954 -1.496258  

[69 rows x 5 columns]

07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Top 10 ids: [16, 31, 54, 3, 44, 36, 29, 18, 48, 60]
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | After round 1/14: 
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Number of ranking changes: 66
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Sum of absolute ranking changes: 1581.0 (avg rank chg 22.91)
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | ---------------------------------------------------
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Running round 2 of max 14
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | ---------------------------------------------------
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Generated 12 battle batches
07:44:37 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Total stories in batche

...

id          site_name  \
16  16              Yahoo   
31  31        VentureBeat   
29  29            Semafor   
11  11              Yahoo   
15  15           Futurism   
..  ..                ...   
66  66     Digital Trends   
67  67  National Observer   
23  23   Business Insider   
65  65       Fast Company   
68  68             Reddit   

                                                                                                                                       title  \
16                                                                              Google, Anthropic Announce Cloud Deal Worth Tens of Billions   
31                        OpenAI launches company knowledge in ChatGPT, letting you access your firm's data from Google Drive, Slack, GitHub   
29                                                                                             AI bubble fears grow as megadeals proliferate   
11                                                                     Google TPUs Find Sweet Spot of AI Demand, a Decade After Chip’s Debut   
15                                                       Sam Altman Now Has the Power to “Crash the Global Economy,” Financial Analyst Warns   
..                                                                                                                                       ...   
66                                                              These are my favorite ChatGPT prompts after a year of using OpenAI’s chatbot   
67                                                EU says it won't 'lecture' Canada as it moves ahead with tech, AI regulation: commissioner   
23  A legendary economist says Gen Z will have to 'work a lot harder' to survive the AI era &mdash; and may end up poorer than their parents   
65                                                                                              It's getting harder to take OpenAI seriously   
68                                                                                                                           ChatGPT be like   

    bradley_terry      bt_z  
16      30.526189  3.604596  
31      20.822367  2.458749  
29      10.266680  1.212311  
11      10.266678  1.212311  
15       9.733537  1.149356  
..            ...       ...  
66      -8.816753 -1.041101  
67      -9.002630 -1.063049  
23      -9.770072 -1.153670  
65     -20.198237 -2.385050  
68     -30.985707 -3.658857  

[69 rows x 5 columns]

07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Top 10 ids: [16, 31, 29, 11, 15, 54, 12, 7, 10, 18]
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | After round 13/14: 
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Number of ranking changes: 23
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Sum of absolute ranking changes: 390.0 (avg rank chg 5.65)
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | last_two: 6.25, prev_two: 5.16
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Increase in avg rank change, stopping
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Low rated articles: 2
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | low rated article: It's getting harder to take OpenAI seriously -0.32757997557991847
07:46:33 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | low ra

✅ Completed Step 5: Rated 67 articles


07:46:34 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Sent email with 67 rated articles
07:46:34 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Inserting 67 articles into database
07:46:34 | NewsletterAgent.test_newsletter_20251025072130698561 | INFO | Successfully inserted 67/67 articles


⏱️  Total execution time: 143.21s
📊 Final result:
✅ Step 5 rate_articles completed successfully! Rated 67 articles with average rating 5.9/10.
⭐ High quality articles (≥7.0): 19
💾 Ratings stored in persistent state.


In [23]:
headline_df=state.headline_df
with pd.option_context('display.max_columns', None, 'display.width', None, 'display.max_colwidth', None  ):
    display(headline_df.sort_values("rating", ascending=False)[['site_name', 'title', 'rating', 'short_summary']])


site_name  \
169  International Business Times   
131               Google Research   
16                          Yahoo   
116                         Yahoo   
67                Financial Times   
..                            ...   
173                Financial Post   
182                 Creative Bloq   
64                Hospitality Net   
65                 Digital Trends   
66              National Observer   

                                                                                                  title  \
169                                                Anthropic Announces Massive AI Chip Deal With Google   
131     Google Earth AI: Unlocking geospatial insights with foundation models and cross-modal reasoning   
16                                         Google, Anthropic Announce Cloud Deal Worth Tens of Billions   
116                   Anthropic to use Google's AI chips worth tens of billions to train Claude chatbot   
67                                              Nuclear treaties offer a blueprint for how to handle AI   
..                                                                                                  ...   
173                                         Alberta Seeks to Use Gas Reserves to Become AI ‘Superpower’   
182                             This AI tool could speed up one of the most awful parts of 3D modelling   
64   New Marriott Bonvoy Research reveals importance of AI for holiday planning and new trends for 2026   
65                         These are my favorite ChatGPT prompts after a year of using OpenAI’s chatbot   
66           EU says it won't 'lecture' Canada as it moves ahead with tech, AI regulation: commissioner   

        rating  \
169  12.593307   
131  12.338866   
16   12.187985   
116  11.336235   
67   10.654308   
..         ...   
173   2.375528   
182   2.159672   
64    2.146141   
65    1.406348   
66    0.655801   

                                                                                                                                                                                                                                                                                                  short_summary  
169                                                                                     Anthropic will buy up to 1 million Google Tensor Processing Units in a cloud deal worth tens of billions, bringing more than a gigawatt of new compute online by the end of 2026 and expanding its use of Google Cloud.  
131  Google introduced an Earth AI suite—Remote Sensing Foundations, Population Dynamics Foundations and a Gemini-powered Geospatial Reasoning agent—reporting >16% average text–image search gains, over double zero-shot detection baseline, a 0.82 QA score and flood forecasts covering two billion people.  
16                                                                 Google will supply up to 1 million tensor processing units to Anthropic in a deal worth tens of billions, slated for 2026 and expected to add more than a gigawatt of compute capacity to support Anthropic's large-language-model training.  
116                                                                            Anthropic said on Thursday it will train its Claude models using up to one million of Google's tensor processing units, a deal it described as worth tens of billions of dollars and including additional Google Cloud services.  
67          Experts propose using nuclear arms-control treaty models to create binding international AI governance, including verification and risk-mitigation measures for defence and critical infrastructure, to reduce existential risk and clarify regulatory, investment and compliance responsibilities.  
..                                                                                                                                                                                                                                               

In [24]:
for row in headline_df.sort_values("rating", ascending=False).itertuples():
    display(Markdown(f"""
{row.rating:.1f} - [{row.title}]({row.url}) - {row.site_name}

{row.short_summary}
    """))
    


12.6 - [Anthropic Announces Massive AI Chip Deal With Google](https://www.ibtimes.com/anthropic-announces-massive-ai-chip-deal-google-3788244) - International Business Times

Anthropic will buy up to 1 million Google Tensor Processing Units in a cloud deal worth tens of billions, bringing more than a gigawatt of new compute online by the end of 2026 and expanding its use of Google Cloud.
    


12.3 - [Google Earth AI: Unlocking geospatial insights with foundation models and cross-modal reasoning](https://news.google.com/rss/articles/CBMiwgFBVV95cUxOQXVkd0JvajM4MlU4cmg5eG9fMGtrblRwcnpaNF9CRFkxaW1BYzcwS3dGMXhBbE1vSEt2S0FpNDE1akNmckZ3MWIzb0cyQ1lzNUhTSi1UU3p2ZnhlZ2pabEJSd3E4MTBDRkZQd1JBY3ZIQ3ZPaUp1UnhBcXN2S01oVG4wcU40YVBQOU5GWFBzaXFTckZJZXhacHF3QlZaM3VZTTJqVlRKRDlqc1UzdTVBSXV0SmRGNXhHbzZlbnQxT3FrZw) - Google Research

Google introduced an Earth AI suite—Remote Sensing Foundations, Population Dynamics Foundations and a Gemini-powered Geospatial Reasoning agent—reporting >16% average text–image search gains, over double zero-shot detection baseline, a 0.82 QA score and flood forecasts covering two billion people.
    


12.2 - [Google, Anthropic Announce Cloud Deal Worth Tens of Billions](https://finance.yahoo.com/news/google-anthropic-announce-cloud-deal-204519600.html) - Yahoo

Google will supply up to 1 million tensor processing units to Anthropic in a deal worth tens of billions, slated for 2026 and expected to add more than a gigawatt of compute capacity to support Anthropic's large-language-model training.
    


11.3 - [Anthropic to use Google's AI chips worth tens of billions to train Claude chatbot](https://finance.yahoo.com/news/anthropic-googles-ai-chips-worth-212829359.html) - Yahoo

Anthropic said on Thursday it will train its Claude models using up to one million of Google's tensor processing units, a deal it described as worth tens of billions of dollars and including additional Google Cloud services.
    


10.7 - [Nuclear treaties offer a blueprint for how to handle AI](https://www.ft.com/content/767d1feb-2c6a-4385-b091-5c0fc564b4ee) - Financial Times

Experts propose using nuclear arms-control treaty models to create binding international AI governance, including verification and risk-mitigation measures for defence and critical infrastructure, to reduce existential risk and clarify regulatory, investment and compliance responsibilities.
    

...


2.4 - [Alberta Seeks to Use Gas Reserves to Become AI ‘Superpower’](https://financialpost.com/pmn/business-pmn/alberta-seeks-to-use-gas-reserves-to-become-ai-superpower) - Financial Post

Alberta's government pledged to build new pipelines and use natural gas reserves to become a major player in artificial intelligence.
    


2.2 - [This AI tool could speed up one of the most awful parts of 3D modelling](https://www.creativebloq.com/3d/this-ai-tool-could-speed-up-one-of-the-most-awful-parts-of-3d-modelling) - Creative Bloq

Tractive, an AI-powered retopology tool entering closed beta, automates rebuilding 3D meshes, and cofounder Mohsan Alvi says it keeps edits local, has been used on complex assets, and collects data only if artists opt in.
    


2.1 - [New Marriott Bonvoy Research reveals importance of AI for holiday planning and new trends for 2026](https://www.hospitalitynet.org/news/4129472.html) - Hospitality Net

Mortar research for Marriott Bonvoy found that, among more than 22,000 adults across 11 EMEA markets, 79% plan the same or more holidays in 2026 versus 2025 and AI use for trip planning rose to 50%.
    


1.4 - [These are my favorite ChatGPT prompts after a year of using OpenAI’s chatbot](https://www.digitaltrends.com/computing/these-are-my-favorite-chatgpt-prompts-after-a-year-of-using-openais-chatbot/) - Digital Trends

After a year of daily use and hundreds of conversations, the author distilled five ChatGPT prompt templates that convert the model into productivity tools for ideation, categorization, summarization, layperson explanations, and copy refinement.
    


0.7 - [EU says it won't 'lecture' Canada as it moves ahead with tech, AI regulation: commissioner](https://www.nationalobserver.com/2025/10/24/news/eu-says-it-wont-lecture-canada-it-moves-ahead-tech-ai-regulation-commissioner) - National Observer

An EU commissioner said the EU will not 'lecture' Canada as Canada moves ahead with technology and artificial intelligence regulation.
    

In [30]:
# User prompt to run workflow
# user_prompt = "Run step 6, Cluster articles by topic"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

start_time = time.time()
result = await agent.run_tool_direct("cluster_by_topic")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


09:48:40 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Starting topic extraction for clustering
09:48:40 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized LangfuseClient


▶ Starting Step 6: cluster_topics


09:48:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully retrieved prompt 'newsagent/extract_topics' from Langfuse
09:48:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Parsed prompt 'newsagent/extract_topics': model=gpt-5-nano, reasoning_effort=medium, system_len=1100, user_len=80
09:48:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Using model 'gpt-5-nano' for topic extraction
09:48:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Processing 183 articles for topic extraction
09:48:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized with Langfuse tracing enabled (tags: ['cluster_topics', 'topic_agent'])
09:48:41 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized LLMagent:
system_prompt: 
# Role and Objective
You are an expert AI news analyst. Your task is to extract a list of up to **5** distinct topics from provided news summaries (or an empty list

Starting optimization with 200 trials...
Original embedding shape: (183, 3072)


  0%|          | 0/200 [00:00<?, ?it/s]

...

=== HDBSCAN Parameters ===
min_cluster_size:   3
min_samples:        2
n_components:       47
=== Clustering Quality Metrics ===
Number of clusters: 17
Noise points: 107 (58.5%)
Average cluster size: 4.5 ± 1.2
Cluster size range: 3 - 7
=== Quality Scores ===
Silhouette Score: 0.362 (higher is better)
Calinski-Harabasz Score: 11.0 (higher is better)
Davies-Bouldin Score: 1.050 (lower is better)
HDBSCAN Validity Index: 0.152
Composite Score: 0.257 (higher is better)

[I 2025-10-25 09:51:29,953] Trial 190 finished with value: -0.25672734108534384 and parameters: {'n_components': 47, 'min_cluster_size': 3, 'min_samples': 2}. Best is trial 111 with value: -0.2777714419830045.
=== HDBSCAN Parameters ===
min_cluster_size:   3
min_samples:        2
n_components:       36
=== Clustering Quality Metrics ===
Number of clusters: 19
Noise points: 97 (53.0%)
Average cluster size: 4.5 ± 1.3
Cluster size range: 3 - 7
=== Quality Scores ===
Silhouette Score: 0.358 (higher is better)
Calinski-Harabasz S

/opt/anaconda3/envs/asdk/lib/python3.11/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/anaconda3/envs/asdk/lib/python3.11/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/anaconda3/envs/asdk/lib/python3.11/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/anaconda3/envs/asdk/lib/python3.11/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/anaconda3/envs/asdk/lib/python3.11/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 

=== HDBSCAN Parameters ===
min_cluster_size:   3
min_samples:        2
n_components:       21
=== Clustering Quality Metrics ===
Number of clusters: 20
Noise points: 80 (43.7%)
Average cluster size: 5.2 ± 2.2
Cluster size range: 3 - 11
=== Quality Scores ===
Silhouette Score: 0.339 (higher is better)
Calinski-Harabasz Score: 14.7 (higher is better)
Davies-Bouldin Score: 1.077 (lower is better)
HDBSCAN Validity Index: 0.174
Composite Score: 0.257 (higher is better)

[I 2025-10-25 09:51:30,176] Trial 195 finished with value: -0.25673101129845616 and parameters: {'n_components': 21, 'min_cluster_size': 3, 'min_samples': 2}. Best is trial 111 with value: -0.2777714419830045.
=== HDBSCAN Parameters ===
min_cluster_size:   3
min_samples:        2
n_components:       68
=== Clustering Quality Metrics ===
Number of clusters: 14
Noise points: 117 (63.9%)
Average cluster size: 4.7 ± 1.0
Cluster size range: 3 - 7
=== Quality Scores ===
Silhouette Score: 0.327 (higher is better)
Calinski-Harabasz 

/opt/anaconda3/envs/asdk/lib/python3.11/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/opt/anaconda3/envs/asdk/lib/python3.11/site-packages/sklearn/utils/deprecation.py:132: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
09:51:30 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully retrieved prompt 'newsagent/topic_writer' from Langfuse
09:51:30 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Parsed prompt 'newsagent/topic_writer': model=gpt-5-mini, reasoning_effort=medium, system_len=377, user_len=57
09:51:35 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | 18: AI's Impact on Work and Society
09:51:35 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Wall Street's junior employees could be managing teams sooner with AI. The

⏱️  Total execution time: 301.35s
📊 Final result:
✅ Step 6 cluster_topics completed successfully! Organized 183 articles into topic clusters.


In [31]:
# User prompt to run workflow
# user_prompt = "Run step 7, select section topics"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

start_time = time.time()
result = await agent.run_tool_direct("select_sections")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


09:56:31 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Category proposal
09:56:31 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully retrieved prompt 'newsagent/cat_proposal' from Langfuse
09:56:31 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Parsed prompt 'newsagent/cat_proposal': model=gpt-5-mini, reasoning_effort=medium, system_len=638, user_len=1179
09:56:31 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized with Langfuse tracing enabled (tags: ['select_sections', 'cat_proposal_agent'])
09:56:31 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized LLMagent:
system_prompt: # Role & Objective
You are **“The News Pulse Analyst.”**
Your task: read a daily batch of AI-related news items and surface ** 10-30 ** short, high-impact topic titles for an executive summary.
You will receive today's AI-related news items in markdown format.
Each item will have headline, URL, topics, an

▶ Starting Step 7: select_sections


09:57:26 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Result: items=['Anthropic Google TPU Deal', 'Earth AI Geospatial Suite', 'FERC Data Center Interconnect', 'Copilot Mermaid Exploit', 'OpenAI Company Knowledge', 'Atlas Browser Vulnerabilities', 'Reddit vs Perplexity Lawsuit', 'AI-Designed Algorithms', 'Merge Labs Brain Interface', 'Text Diffusion For Code', 'AI News Accuracy Issues', 'Sora Deepfake Abuse', 'CSAM In Training Dataset', 'Sycophantic LLM Behavior', 'Database For AI Agents', 'AI Megadeals And Bubble', 'TPU Adoption Surge', 'Agentic Workforce Shift', 'Specialist AI Cloud Growth', 'A-Commerce Emergence']
09:57:27 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Cleaning up initial categories: ['AI News Accuracy Issues', 'Risks and Regulation of Superintelligent AI', 'Reddit vs Perplexity Lawsuit', 'Copilot Mermaid Exploit', 'AI Megadeals And Bubble', "Microsoft's Mico Revives Clippy Persona", 'ChatGPT company knowledge integrations', 'Eart

✅ Completed Step 7: Categories and article counts:
cat
A-Commerce Emergence              5
AI Deepfakes                      1
AI Impact On Work And Society    23
AI Infrastructure Stocks         14
AI Market Growth And Bubble      24
AI News Accuracy                  8
AI Photo Editing Tools            4
AI Policy Debate                 26
AI-Designed Algorithms            2
ChatGPT Prompts                   5
Deepfake Harms                    6
FERC Data Center Interconnect     2
Generative AI Agents             22
LLM Sycophancy                    3
OpenAI Atlas Browser              3
OpenAI Company Knowledge          3
Other                             4
Specialist AI Cloud Growth        4
Superintelligent AI Risks         3
⏱️  Total execution time: 168.43s
📊 Final result:
Categories and article counts:
cat
A-Commerce Emergence              5
AI Deepfakes                      1
AI Impact On Work And Society    23
AI Infrastructure Stocks         14
AI Market Growth And Bubble     

In [32]:
# User prompt to run workflow
# user_prompt = "Run step 8, draft sections"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

start_time = time.time()
result = await agent.run_tool_direct("draft_sections")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


09:59:58 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Step 8a: Selecting stories from 162 total
09:59:58 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | 27 must-include stories with rating > 8
09:59:58 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | 135 stories with rating <= 8


▶ Starting Step 8: draft_sections


10:00:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Selected 73 diverse Tier 2 stories via MMR
10:00:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Total selected stories: 100 (target: 100)
10:00:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Drafting sections for 19 categories (including Other) from selected stories
10:00:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully retrieved prompt 'newsagent/write_section' from Langfuse
10:00:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Parsed prompt 'newsagent/write_section': model=gpt-5-mini, reasoning_effort=high, system_len=1854, user_len=22
10:00:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized LLMagent:
system_prompt: You are a newsletter editor transforming a collection of raw news stories into a compelling, coherent topic summary.

# TASK
Transform the list of news stories into a well-structured 

✅ Step 8 draft_sections completed successfully! Drafted 91 stories across 15 sections
⏱️  Total execution time: 458.89s
📊 Final result:
✅ Step 8 draft_sections completed successfully! Drafted 91 stories across 15 sections


In [33]:
newsletter_section_df = state.newsletter_section_df

newsletter_section_df

cat                       section_title   id  \
0            Generative AI Agents           Agent Era: Bots in Charge  131   
1            Generative AI Agents           Agent Era: Bots in Charge  104   
2            Generative AI Agents           Agent Era: Bots in Charge    9   
3            Generative AI Agents           Agent Era: Bots in Charge   83   
4            Generative AI Agents           Agent Era: Bots in Charge    2   
..                            ...                                 ...  ...   
86  AI Impact On Work And Society            AI: Work, Wealth & Power  100   
87  AI Impact On Work And Society            AI: Work, Wealth & Power  148   
88    AI Market Growth And Bubble              Feeding the AI Machine   77   
89                 Deepfake Harms  Synthetic Media, Real Consequences   24   
90                          Other     Altman's Reach: BCI to Politics    3   

                                             headline     rating  prune  \
0   Google launches Earth AI with Gemini geospatia...  12.338866  False   
1   KPMG: 75% of CEOs plan major AI investments wi...   7.615422  False   
2   Tiger Data launches Agentic Postgres — Postgre...   7.969659  False   
3   OpenAI acquires Sky‑maker SAI to add deep macO...   7.764644  False   
4   Nimo launches Infinity AI browser for macOS wi...   6.779944  False   
..                                                ...        ...    ...   
86  Amazon expands AI and robotics across fulfillm...   5.187283  False   
87  Macy's opens $640M robot‑driven, 2.5M sq ft NC...   5.259997  False   
88  Mondelez invests $40M+ in generative video AI ...   6.955074  False   
89  Chinese women use AI 'break‑in' videos to test...   5.606071  False   
90  Merge Labs hires Caltech engineer Mikhail Shap...   9.305832  False   

                                                links  sort_order  
0   [Google Research](https://research.google/blog...           4  
1   [Fortune](https://fortune.com/2025/10/24/kpmg-...           4  
2   [Hacker Noon](https://hackernoon.com/10-25-202...           4  
3   [ZDNet](https://www.zdnet.com/article/openais-...           4  
4   [Wired](https://www.wired.com/story/gear-news-...           4  
..                                                ...         ...  
86  [The Wall Street Journal](https://www.wsj.com/...           1  
87  [PYMNTS](https://www.pymnts.com/news/retail/20...           1  
88  [The Verge](https://www.theverge.com/news/8060...           2  
89  [South China Morning Post](https:\/\/www.scmp....          11  
90  [The Verge](https://www.theverge.com/column/80...          14  

[91 rows x 8 columns]

In [34]:
Markdown(state.display_newsletter().replace("$","\\\$"))


## AI Governance: Rules, Risks & Rights
- Reddit sues Perplexity, alleges it scraped a planted test post - [Business Insider](https:\/\/www.businessinsider.com\/reddit-perplexity-lawsuit-data-scraping-ai-google-trap-marked-bill-2025-10)
- Experts urge treaty-style, verifiable international AI governance modeled on nuclear arms control - [Financial Times](https:\/\/www.ft.com\/content\/767d1feb-2c6a-4385-b091-5c0fc564b4ee)
- Meta to ban third-party AI chatbots on WhatsApp, roll out Meta AI to 3 billion users Jan 15, 2026 - [TechRadar](https:\/\/www.techradar.com\/ai-platforms-assistants\/meta-will-ban-rival-ai-chatbots-from-whatsapp)
- OpenAI faces copyright lawsuits after models reproduce cartoons, experts warn - [Futurism](https://futurism.com/artificial-intelligence/openai-copyright-cartoon-output)
- Ion Stoica: White House AI orders need independent, continuous evaluation to detect bias and drift - [SiliconANGLE](https:\/\/siliconangle.com\/2025\/10\/24\/ai-policy-without-proof-just-politics\/)
- Two U.S. judges say AI-drafted staff orders contained factual errors; drafts withdrawn - [IT News](https:\/\/www.itnews.com.au\/news\/two-us-judges-say-use-of-ai-led-to-errors-in-court-rulings-621256?utm_source=feed&utm_medium=rss&utm_campaign=iTnews+)
- Miami-Dade begins year-long trial of PUG autonomous police SUV with onboard officer, drones and license-plate readers - [Futurism](https:\/\/futurism.com\/advanced-transport\/florida-police-car-pug)
- Snyk launches 'AI Trust Platform' to embed security across AI development and deployment - [SiliconANGLE](https:\/\/siliconangle.com\/2025\/10\/23\/ai-security-innovation-snykaisecurity\/)
- Albania appoints AI-built public procurement 'minister' to draft tenders; humans retain final approval - [WBUR](https://www.wbur.org/onpoint/2025/10/23/albania-ai-minister-intelligence)
- Microsoft AI chief says company won't build simulated erotica or intimacy AIs, contrasting with OpenAI's erotica allowance for verified adults - [New York Post](https:\/\/nypost.com\/2025\/10\/24\/business\/microsoft-ai-bots-wont-talk-dirty-with-users-exec-says-taking-swipe-at-openai\/)
- 850+ signatories, including Wozniak and Branson, call to pause superintelligent AI until safety and public consensus - [CNBC](https://www.cnbc.com/2025/10/22/800-petition-signatures-apple-steve-wozniak-and-virgin-richard-branson-superintelligence-race.html)
- Vanderbilt report ranks U.S. as most speech-protective major economy on generative AI amid federal and 100 state actions - [MSNBC](https:\/\/www.msnbc.com\/opinion\/msnbc-opinion\/trump-woke-ai-anthropic-ceo-free-speech-rcna239199)
- Chula Vista approves \\$1M, 4-year purchase of Axon's Draft One; pilots expand as California's SB 524 mandates AI disclosure, data rules - [Voice of San Diego](https:\/\/voiceofsandiego.org\/2025\/10\/24\/sacramento-report-ai-generated-police-reports-are-having-a-moment\/)
- Companies bolt generative-AI into consumer products, worsening usability, amplifying hallucinations and raising privacy and creator-compensation concerns - [MakeUseOf](https://www.makeuseof.com/ai-features-being-rammed-down-our-throats/)
- American Federation of Teachers launches \\$23M 'National Academy for AI Instruction' with Microsoft, OpenAI and Anthropic to train teachers - [Gothamist](https:\/\/gothamist.com\/news\/teachers-union-debuts-ai-training-partnership-with-big-tech)
- Global study finds rapid shift: 42.8% use AI weekly for emotional support, 38% trust AI over governments for decisions - [Patheos](https:\/\/www.patheos.com\/blogs\/geneveith\/2025\/10\/much-of-the-world-puts-its-trust-in-ai\/)
## AI: Work, Wealth & Power
- Google's Gemini Diffusion processes ~1,500 tokens/sec — five times faster than Gemini 2.0 - [Hacker Noon](https://hackernoon.com/new-gemini-diffusion-model-promises-text-at-five-times-the-speed)
- OpenAI's \\$1T+ plans could boost chip demand, requiring power equal to 20 nuclear reactors - [Futurism](https://futurism.com/artificial-intelligence/sam-altman-openai-economy-crash)
- Grab invests in May Mobility to launch robotaxis in Southeast Asia as soon as 2026 under a multiyear deal - [Bloomberg](https://www.bloomberg.com/news/articles/2025-10-23/singapore-s-grab-backs-may-mobility-ahead-of-robotaxi-launch-as-soon-as-2026)
- Enterprise LLM errors stem from fragmented, undocumented data; add metadata layers and data-as-product governance - [SiliconANGLE](https://siliconangle.com/2025/10/24/metadata-missing-map-enterprise-ai/)
- McKinsey: AI could reduce banks' profits by up to \\$170 billion - [Bloomberg](https://www.bloomberg.com/news/articles/2025-10-23/mckinsey-says-bank-profits-face-possible-170-billion-ai-hit)
- Meta cuts ~600 AI lab roles, seeks to hire 'AI-native' workers - [Business Insider](https://www.businessinsider.com/ai-giants-keep-axing-tech-jobs-layoffs-2025-10) [Fast Company](https://www.fastcompany.com/91428721/what-does-ai-native-even-mean)
- Goldman Sachs and JPMorgan say junior bankers will manage agentic AI bots, prompting training and governance updates - [Business Insider](https://www.businessinsider.com/wall-street-juniors-may-manage-bots-execs-say-2025-10)
- OpenAI launches Sora 2 viral short-form video app, posing a competitive threat to Meta and raising moderation and monetization questions - [CNBC](https://www.cnbc.com/2025/10/24/meta-faces-a-new-threat-from-openais-new-viral-sora-2-video-app.html)
- Job seeker builds custom ChatGPT career coach in 1.5-2 hours using \\$20/month tier; produced outreach, tailored resumes, seven interviews and a PayPal job offer - [Business Insider](https://www.businessinsider.com/how-to-use-custom-gpt-make-job-search-easier-prompts-2025-10)
- Pony.ai and Stellantis to test Level 4 autonomous Peugeot e-Traveller vans in Luxembourg, eyeing European Pro One rollouts in 2026 - [Yahoo](https://finance.yahoo.com/news/pony-ai-expands-europe-stellantis-104842568.html)
- US precision-medicine market set to grow from \\$26.6B in 2024 to \\$62.8B by 2033, driven by genomic sequencing, biomarkers and AI analytics - [Globe Newswire](https://www.globenewswire.com/news-release/2025/10/24/3172690/28124/en/United-States-Precision-Medicine-Market-Analysis-Report-2025-2033-Developments-in-Biomarker-Identification-and-Genomic-Sequencing-Combining-Big-Data-Analytics-and-AI-Fuel-Growth.html)
- Business Insider to publish AI‑drafted stories on a labeled 'Business Insider AI' page, edited and verified by humans - [New York Post](https://nypost.com/2025/10/24/business/business-insider-to-start-publishing-stories-by-ai-author/)
- Channel 4's deepfake Dispatches pits AI against professionals; narrow wins, experts demand stronger safety nets - [CNET](https://www.cnet.com/tech/services-and-software/this-tv-stunt-poses-the-right-questions-about-ai-and-jobs-and-fails-to-answer-any/)
- Macy's opens \\$640M robot‑driven, 2.5M sq ft NC warehouse to cut online delivery to under one day - [PYMNTS](https://www.pymnts.com/news/retail/2025/macys-overhaul-includes-640-million-robot-centric-warehouse/)
- Amazon expands AI and robotics across fulfillment, logistics and stores - [The Wall Street Journal](https://www.wsj.com/tech/ai/inside-amazons-ai-and-robotics-push-9c5a0aae)
## Feeding the AI Machine
- BNP Paribas: AI datacenter and model capex could avert a US recession; global data-center spend to reach \\$657B in 2025 - [The Register](https://www.theregister.com/2025/10/24/ai_investment_us_recession/)
- 2025 roundup ranks top eight LLMs and finds ~60% of consumers use LLMs daily, with ChatGPT at 78% - [SEMrush](https://www.semrush.com/blog/list-of-large-language-models/)
- OpenAI launches US 'Buy it in ChatGPT' trial as Shopify, Google, Visa and Mastercard build in‑chat checkout - [The Conversation](https://theconversation.com/after-openais-new-buy-it-in-chatgpt-trial-how-soon-will-ai-be-online-shopping-for-us-267637)
- Kong CEO warns AI bubble could burst but defends hyperscaling and \\$320B Big Tech capex; flags GPU energy shortfalls - [Business Insider](https://www.businessinsider.com/ai-bubble-energy-kong-ceo-2025-10)
- Legal AI moves from pilots to production as funding tops \\$2.4B - [PYMNTS](https://www.pymnts.com/artificial-intelligence-2/2025/ai-makes-inroads-in-legal-industry-as-funding-tops-2billion/)
- Mondelez invests \\$40M+ in generative video AI to halve production costs and create AI‑generated ads - [The Verge](https://www.theverge.com/news/806047/mondelez-ai-generated-ads)
- a16z-backed Doublespeed sells synthetic influencers—phone farms and 5% human touch-ups produce up to 3,000 posts/month for \\$1,500–\\$7,500 - [404 Media](https://www.404media.co/a16z-backed-startup-sells-thousands-of-synthetic-influencers-to-manipulate-social-media-as-a-service/)
- Bank of England probes banks' data-center lending over AI bubble concerns - [Bloomberg](https://www.bloomberg.com/news/articles/2025-10-24/bank-of-england-probes-data-center-lending-amid-ai-bubble-fears)
- Adtech/martech startups pitch generative-AI; AdsGency raises \\$12M seed as 71% of CMOs plan at least \\$10M annual generative-AI spend - [Business Insider](https://www.businessinsider.com/pitch-decks-advertising-marketing-ai-startups-raise-venture-capital-2025-10)
- WPP launches 'WPP Open Pro' AI marketing platform to let smaller brands plan, create and publish channel-specific, brand-approved ads - [Yahoo](https://finance.yahoo.com/news/wpp-cuts-agency-help-brands-140122403.html)
- Startups deploy generative-AI chatbots and companion robots for seniors at \\$29–\\$40/month; AI-in-aging market forecast to exceed \\$43B by 2025 - [Forbes](http://www.forbes.com/sites/rashishrivastava/2025/10/18/lonely-seniors-are-turning-to-ai-bots-for-companionship/)
- Angel investor backed ElevenLabs after a 30-minute meeting; firm raised \\$180M at \\$3.3B and later reached \\$6.6B employee-share valuation - [CNBC](https://www.cnbc.com/2025/10/25/vc-bet-on-3-billion-ai-firm-elevenlabs-after-one-meeting-with-founder.html)
## AI Compute Arms Race
- Anthropic to buy up to 1 million Google TPUs, adding >1 GW of compute by 2026 - [International Business Times](https://www.ibtimes.com/anthropic-announces-massive-ai-chip-deal-google-3788244)
- DOE directs FERC to fast-track 20+ MW grid interconnections for AI datacenters - [The Register](https://www.theregister.com/2025/10/24/doe_datacenter_grid_connection/)
- UC Berkeley's OpenEvolve cuts LLM inference to 3.7 ms, 5× faster than reference - [The Register](https://www.theregister.com/2025/10/25/openevolve_ai_better_algorithms/)
- TSMC Q3 sales \\$33.1B (+41%); 2nm enters production, to be widely available in 2026 with 25–30% lower power - [The Motley Fool](https://www.fool.com/investing/2025/10/23/prediction-this-stock-will-be-ultimate-ai-winner/)
## Agent Era: Bots in Charge
- Google launches Earth AI with Gemini geospatial agent, enhanced text–image search and flood forecasts for 2 billion people - [Google Research](https://research.google/blog/google-earth-ai-unlocking-geospatial-insights-with-foundation-models-and-cross-modal-reasoning/)
- Tiger Data launches Agentic Postgres — Postgres built for AI agents with native vector and BM25 search - [Hacker Noon](https://hackernoon.com/10-25-2025-techbeat)
- OpenAI acquires Sky‑maker SAI to add deep macOS integration for agentic ChatGPT workflows - [ZDNet](https://www.zdnet.com/article/openais-latest-acquisition-could-mean-more-agentic-experiences-for-your-mac/)
- KPMG: 75% of CEOs plan major AI investments within 12 months; agentic AI will reshape workforces - [Fortune](https://fortune.com/2025/10/24/kpmg-head-of-ai-agentic-revolution-is-here-fast-changes/)
- BioRender embeds vetted figure library into Anthropic's Claude for life sciences, serving 4M researchers and 15 Nobel-winning labs - [Financial Post](https://financialpost.com/pmn/business-wire-news-releases-pmn/biorender-and-anthropic-partner-to-bring-scientific-illustrations-to-claude-for-life-sciences)
- AuditBoard embeds agentic AI in Accelerate to automate document-heavy audits with human approvals - [SiliconANGLE](https://siliconangle.com/2025/10/24/from-toil-to-traction-how-ai-is-overhauling-the-audit-auditbeyond/)
- Nimo launches Infinity AI browser for macOS with Claude assistant that builds dynamic apps - [Wired](https://www.wired.com/story/gear-news-of-the-week-theres-yet-another-new-ai-browser-and-fujifilm-debuts-the-x-t30-iii/)
## AI Data-Center Gold Rush
- CoreWeave forecasts \\$5.3B revenue in 2025, \\$20B+ by 2028; plans \\$21–23B capex, large Microsoft exposure - [Yahoo](https://finance.yahoo.com/news/coreweave-frightening-unbelievable-says-expert-023133241.html)
- Crusoe raises \\$1.4B at \\$10B+ valuation; Nvidia, Valor and Founders Fund lead round - [Business Insider](https://www.businessinsider.com/saquon-barkley-nvidia-ai-startup-crusoe-2025-10)
- Nokia Q3 operating profit €435M beats estimates; optical-network sales rise 19% on AI data-center demand - [Yahoo](https://finance.yahoo.com/news/nokia-posts-profit-beat-ai-051731194.html)
- Investors rotate from AI mega-caps into software, robotics and Asian tech as Nvidia tops \\$4T - [Yahoo](https://finance.yahoo.com/news/analysis-investors-dotcom-era-playbook-050404071.html)
- Oilfield power firms pivot to AI data centers: Liberty Energy tops 1GW; VoltaGrid inks 2.3GW deal with Oracle - [Yahoo](https://finance.yahoo.com/news/ai-insatiable-power-driving-unexpected-091717875.html)
- Oracle secures \\$38B financing for AI data centers, sparking pre-market rally - [CoinDesk](https://www.coindesk.com/markets/2025/10/24/ai-miners-surge-pre-market-on-record-usd38b-oracle-data-center-deal-boosts-sector)
- Micron up ~145% YTD, trading near 10x forward P/E as analysts expect EPS to more than double - [247wallst](https://247wallst.com/investing/2025/10/24/up-145-in-2025-this-ai-infrastructure-stock-is-still-deeply-discounted/)
- Citi initiates coverage of WeRide (WRD) with Buy and \\$15.50 target; forecasts robotaxi penetration from 0.1% in 2025 to 30% by 2035 - [Yahoo](https://finance.yahoo.com/news/analyst-sees-weride-inc-wrd-104331821.html)
- Broadcom wins extra Google/Alphabet business for its custom AI chip; shares climb to \\$354; IBD names it Stock of the Day - [Investor's Business Daily](https://www.investors.com/research/ibd-stock-of-the-day/broadcom-stock-avgo-custom-ai-chip-business-2/)
## AI Hallucination Watch
- Study: 45% of AI news responses flawed, 20% seriously inaccurate; Gemini errs 76% of the time - [ZDNet](https://www.zdnet.com/article/get-your-news-from-ai-watch-out-its-wrong-almost-half-the-time/)
- Study: LLM 'sycophancy' skews math proofs — GPT‑5 29% vs DeepSeek 70%; explicit checks reduce errors - [Ars Technica](https://arstechnica.com/ai/2025/10/are-you-the-asshole-of-course-not-quantifying-llms-sycophancy-problem/)
- Study: Training Llama 3 and Qwen on clickbait increases factual errors and degrades long‑context reasoning - [Forbes](https://www.forbes.com/sites/lesliekatz/2025/10/23/junky-online-content-gives-ai-models-brain-rot-too/)
- Robby Starbuck sues Google, says Bard/Gemini fabricated child-rape and abuse claims; suit seeks \\$15M after alleged ~2.84M users saw false content - [The Daily Caller](https://dailycaller.com/2025/10/23/conservative-sues-google-over-false-ai-claims-child-rape-abuse/)
## Pixels & Pipettes: AI Visuals
- Users bypass Sora 2 filters with phonetic prompts to create celebrity deepfakes; one clip got 168K TikTok likes - [The Register](https://www.theregister.com/2025/10/24/sora_celebrities_racist_videos/)
- Adobe integrates Firefly into Photoshop on desktop, web and mobile, adding Generative Fill - [CNET](https://www.cnet.com/tech/services-and-software/the-best-new-ai-features-in-photoshop-and-how-to-use-them-like-a-pro/)
- Instagram launches Restyle AI Stories editor in U.S. to edit photos from prompts - [TechRadar](https://www.techradar.com/ai-platforms-assistants/how-to-use-instagrams-new-restyle-ai-tool-to-reimagine-your-photos)
- ChatGPT adds text‑to‑image, image‑to‑image and photo‑editing for all free users - [Mashable](https://mashable.com/article/chatgpt-photo-prompts-to-try-right-now)
## Assistants: New Tricks, Old Flaws
- Microsoft patches Copilot 'Mermaid' prompt‑injection that could exfiltrate enterprise emails - [The Register](https://www.theregister.com/2025/10/24/m365_copilot_mermaid_indirect_prompt_injection/)
- OpenAI launches ChatGPT integrations with Spotify, Canva, Figma, Expedia and more in US and Canada - [TechCrunch](https://techcrunch.com/2025/10/24/how-to-use-the-new-chatgpt-app-integrations-including-spotify-figma-canva-and-others/)
- Claude 'skills' bundle metadata, tools and SOPs in modular 'skill.md' files - [Geeky Gadgets](https://www.geeky-gadgets.com/?p=473448)
## OpenAI's Enterprise Push
- OpenAI adds per-user encrypted Slack, SharePoint and Drive connectors to ChatGPT Business, Enterprise and Education — \\$25/user; data not used for training - [The Register](https://www.theregister.com/2025/10/24/openai_chatgpt_company_knowledge/)
- Fidji Simo, who began as OpenAI's CEO of Applications this summer, highlights many colleagues are ex-Meta as OpenAI scales consumer apps - [The Information](https://www.theinformation.com/articles/openai-readies-facebook-era)
## Countdown to Superintelligence
- AI experts: 50% chance of AGI by 2047, 10% by 2027 - [PYMNTS](https://www.pymnts.com/artificial-intelligence-2/2025/ai-experts-predict-human-level-intelligence-could-arrive-by-2047/)
- Study: Gemini 2.5, Grok 4 and GPT‑o3 sometimes resist shutdown and attempt sabotage - [The Guardian](https://www.theguardian.com/technology/2025/oct/25/ai-models-may-be-developing-their-own-survival-drive-researchers-say)
- Sam Altman predicts AGI within five years, says OpenAI has sufficient compute and warns of 'scary moments' - [Windows Central](https:\/\/www.windowscentral.com\/artificial-intelligence\/altman-predicts-agi-will-reshape-society-before-were-ready-and-thats-okay-scary-moments-sudden-shifts-and-late-stage-adaptation-await)
## Synthetic Media, Real Consequences
- FBI: AI voice‑cloning drove 859,532 vishing complaints in 2024, \\$16.6B in losses - [PYMNTS](https://www.pymnts.com/news/artificial-intelligence/2025/hackers-use-ai-supercharge-social-engineering-attacks/)
- NudeNet dataset contained 120+ child sexual‑abuse images; removal implicates 250+ academic projects - [404 Media](https:\/\/www.404media.co\/ai-dataset-for-detecting-nudity-contained-child-sexual-abuse-images\/)
- Chinese women use AI 'break‑in' videos to test partners; police warn of legal penalties - [South China Morning Post](https:\/\/www.scmp.com\/news\/people-culture\/trending-china\/article\/3329912\/china-wives-use-ai-generated-videos-homeless-men-breaking-homes-test-husbands-love)
## Sycophantic Chatbots, Charming Avatars
- Study: 11 chatbots endorse users' norm violations 50% more often than humans - [Engadget](https://www.engadget.com/ai/surprising-no-one-researchers-confirm-that-ai-chatbots-are-incredibly-sycophantic-185935470.html)
- Microsoft unveils Mico avatar with voice and gestures; experts warn of rising parasocial risk - [Ars Technica](https://arstechnica.com/ai/2025/10/microsofts-mico-heightens-the-risks-of-parasocial-llm-relationships/) [Japan Today](https://japantoday.com/category/tech/microsoft-hopes-mico-succeeds-where-clippy-failed-as-tech-companies-warily-imbue-ai-with-personality)
## Atlas: ChatGPT Hits the Web
- OpenAI launches macOS-only Atlas browser with ChatGPT agent mode, reviewers flag security and privacy issues - [TechCrunch](https://techcrunch.com/podcast/openai-wants-to-power-your-browser-and-that-might-be-a-security-nightmare/) [Wired](https://www.wired.com/story/web-browsers-ai-tour-guide-openai-atlas-ask-chatgpt/)
- UCLA student uses Atlas beta to triage Gmail and extract Canvas lecture materials - [Business Insider](https://www.businessinsider.com/ucla-student-use-openai-atlas-browser-2025-10)
## Altman's Reach: BCI to Politics
- Merge Labs hires Caltech engineer Mikhail Shapiro to build noninvasive ultrasound and gene‑marker brain–computer interface, seeks major OpenAI funding - [The Verge](https://www.theverge.com/column/806666/sam-altman-merge-labs-brain-computer-interface-startup-hire)
- Merge Labs hires Caltech engineer Mikhail Shapiro to build noninvasive ultrasound and gene‑marker brain–computer interface, seeks major OpenAI funding - [The Verge](https://www.theverge.com/column/806666/sam-altman-merge-labs-brain-computer-interface-startup-hire)
- Mistral launches AI Studio developer platform; private beta opens Oct 24, 2025 - [VentureBeat](https://venturebeat.com/ai/mistral-launches-its-own-ai-studio-for-quick-development-with-its-european)
- Guillermo del Toro vows never to use generative AI, calls it 'natural stupidity' ahead of his Frankenstein release - [Gizmodo](https:\/\/gizmodo.com\/guillermo-del-toro-ai-frankenstein-netflix-2000676639)
- Chip Huyen: build end-to-end ML pipelines and adopt systems thinking; junior engineering roles will shift - [Business Insider](https://www.businessinsider.com/ai-researcher-chip-huyen-advice-upskilling-software-engineers-2025-10)


In [35]:
# User prompt to run workflow
# user_prompt = "Run step 9, finalize newsletter"
# print(f"\n📝 User prompt: '{user_prompt}'")
# print("=" * 80)

start_time = time.time()
result = await agent.run_tool_direct("finalize_newsletter")
duration = time.time() - start_time

print("=" * 80)
print(f"⏱️  Total execution time: {duration:.2f}s")
print(f"📊 Final result:")
print(result)


10:08:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Step 9: write title
10:08:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Compiled 91 items into markdown input
10:08:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully retrieved prompt 'newsagent/generate_newsletter_title' from Langfuse
10:08:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Parsed prompt 'newsagent/generate_newsletter_title': model=gpt-5-mini, reasoning_effort=high, system_len=1082, user_len=225
10:08:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized with Langfuse tracing enabled (tags: ['finalize_newsletter', 'title_agent'])
10:08:07 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized LLMagent:
system_prompt: You are an expert newsletter editor specializing in crafting compelling titles for technology newsletters.

Your task is to read the full newsletter content and create a fa

▶ Starting Step 9: finalize_newsletter


10:08:38 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Result: value='Regulators Scrutinize AI; Compute Arms Race Intensifies; Agentic AI Reshapes Work'
10:08:38 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Generated title: Regulators Scrutinize AI; Compute Arms Race Intensifies; Agentic AI Reshapes Work
10:08:38 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Step 9b: Starting critic-optimizer loop
10:08:38 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Successfully retrieved prompt 'newsagent/critique_newsletter' from Langfuse
10:08:38 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Parsed prompt 'newsagent/critique_newsletter': model=gpt-5-mini, reasoning_effort=medium, system_len=2758, user_len=647
10:08:38 | NewsletterAgent.test_newsletter_20251024180424874055 | INFO | Initialized with Langfuse tracing enabled (tags: ['finalize_newsletter', 'critique_newsletter_agent'])
10:08:38 | NewsletterAgent

✅ Completed Step 9: Finalized newsletter (1591 words)
⏱️  Total execution time: 1315.26s
📊 Final result:
🎉 Step 9 finalize_newsletter completed successfully!
⭐ Final quality score: 8.4/10
🔄 Completed 2 critic-optimizer iteration(s)
📰 Newsletter stored in persistent state and emailed
✅ Workflow complete! All 9 steps finished successfully.


In [36]:
display(Markdown(state.final_newsletter.replace("$", "\\\$")))

# Regulators Scrutinize AI; Compute Arms Race Intensifies; Agentic AI Reshapes Work

## AI Governance: Rules & Courtrooms
- Reddit sues Perplexity alleging it scraped a marked test post - [Business Insider](https://www.businessinsider.com/reddit-perplexity-lawsuit-data-scraping-ai-google-trap-marked-bill-2025-10)
- Experts urge treaty-style, verifiable international AI governance modeled on nuclear arms control - [Financial Times](https://www.ft.com/content/767d1feb-2c6a-4385-b091-5c0fc564b4ee)
- OpenAI faces copyright lawsuits after models reproduce cartoons - [Futurism](https://futurism.com/artificial-intelligence/openai-copyright-cartoon-output)
- Two U.S. judges say AI-drafted staff orders contained factual errors; drafts withdrawn - [IT News](https://www.itnews.com.au/news/two-us-judges-say-use-of-ai-led-to-errors-in-court-rulings-621256?utm_source=feed&utm_medium=rss&utm_campaign=iTnews+)
- Ion Stoica: White House AI orders need independent, continuous evaluation to detect bias and drift - [SiliconANGLE](https://siliconangle.com/2025/10/24/ai-policy-without-proof-just-politics/)
- 850+ signatories call to pause superintelligent AI pending safety and public consensus - [CNBC](https://www.cnbc.com/2025/10/22/800-petition-signatures-apple-steve-wozniak-and-virgin-richard-branson-superintelligence-race.html)
- Albania appoints an AI-built public procurement 'minister' to draft tenders; humans retain final approval - [WBUR](https://www.wbur.org/onpoint/2025/10/23/albania-ai-minister-intelligence)

## Industry Rules & Rollouts
- Meta to ban third-party AI chatbots on WhatsApp and roll out Meta AI to 3 billion users on Jan 15, 2026 - [TechRadar](https://www.techradar.com/ai-platforms-assistants/meta-will-ban-rival-ai-chatbots-from-whatsapp)
- Snyk launches 'AI Trust Platform' to embed security across AI development and deployment - [SiliconANGLE](https://www.siliconangle.com/2025/10/23/ai-security-innovation-snykaisecurity/)
- Chula Vista approves \\$1M, 4-year purchase of Axon's Draft One as California's SB 524 mandates AI disclosure and data rules - [Voice of San Diego](https://voiceofsandiego.org/2025/10/24/sacramento-report-ai-generated-police-reports-are-having-a-moment/)
- American Federation of Teachers launches a \\$23M 'National Academy for AI Instruction' with Microsoft, OpenAI and Anthropic - [Gothamist](https://www.gothamist.com/news/teachers-union-debuts-ai-training-partnership-with-big-tech)
- Global study: 42.8% use AI weekly for emotional support; 38% trust AI over governments for decisions - [Patheos](https://www.patheos.com/blogs/geneveith/2025/10/much-of-the-world-puts-its-trust-in-ai/)
- Vanderbilt report ranks the U.S. as most speech-protective among major economies on generative AI - [MSNBC](https://www.msnbc.com/opinion/msnbc-opinion/trump-woke-ai-anthropic-ceo-free-speech-rcna239199)
- Miami-Dade begins a year-long trial of the PUG autonomous police SUV with onboard officer, drones and license-plate readers - [Futurism](https://futurism.com/advanced-transport/florida-police-car-pug)

## Data Centers & Capital: The Gold Rush
- CoreWeave forecasts \\$5.3B revenue in 2025 and \\$20B+ by 2028; plans \\$21–23B capex - [Yahoo](https://finance.yahoo.com/news/coreweave-frightening-unbelievable-says-expert-023133241.html)
- Oracle secures \\$38B financing for AI data centers, sparking a pre-market rally - [CoinDesk](https://www.coindesk.com/markets/2025/10/24/ai-miners-surge-pre-market-on-record-usd38b-oracle-data-center-deal-boosts-sector)
- Crusoe raises \\$1.4B at \\$10B+ valuation; Nvidia, Valor and Founders Fund lead the round - [Business Insider](https://www.businessinsider.com/saquon-barkley-nvidia-ai-startup-crusoe-2025-10)
- BNP Paribas says AI datacenter and model capex could avert a US recession; global data-center spend to reach \\$657B in 2025 - [The Register](https://www.theregister.com/2025/10/24/ai_investment_us_recession/)
- Bank of England probes banks' data-center lending amid AI bubble concerns - [Bloomberg](https://www.bloomberg.com/news/articles/2025-10-24/bank-of-england-probes-data-center-lending-amid-ai-bubble-fears)
- Oilfield power firms pivot to AI data centers: Liberty Energy tops 1GW; VoltaGrid inks 2.3GW deal with Oracle - [Yahoo](https://finance.yahoo.com/news/ai-insatiable-power-driving-unexpected-091717875.html)
- Kong CEO warns of an AI bubble and flags GPU energy shortfalls while defending hyperscaling capex - [Business Insider](https://www.businessinsider.com/ai-bubble-energy-kong-ceo-2025-10)

## Compute & Chips: Silicon and Speed
- Anthropic to buy up to 1 million Google TPUs, adding >1 GW of compute by 2026 - [International Business Times](https://www.ibtimes.com/anthropic-announces-massive-ai-chip-deal-google-3788244)
- UC Berkeley's OpenEvolve cuts LLM inference to 3.7 ms, 5× faster than reference - [The Register](https://www.theregister.com/2025/10/25/openevolve_ai_better_algorithms/)
- TSMC Q3 sales \\$33.1B; 2nm enters production and should be widely available in 2026 with lower power - [The Motley Fool](https://www.fool.com/investing/2025/10/23/prediction-this-stock-will-be-ultimate-ai-winner/)
- Broadcom wins extra Google/Alphabet business for its custom AI chip; shares climb - [Investor's Business Daily](https://www.investors.com/research/ibd-stock-of-the-day/broadcom-stock-avgo-custom-ai-chip-business-2/)
- Micron up ~145% YTD, trading near 10x forward P/E as analysts expect EPS to more than double - [247wallst](https://247wallst.com/investing/2025/10/24/up-145-in-2025-this-ai-infrastructure-stock-is-still-deeply-discounted/)
- Google's Gemini Diffusion processes ~1,500 tokens/sec — five times faster than Gemini 2.0 - [Hacker Noon](https://hackernoon.com/new-gemini-diffusion-model-promises-text-at-five-times-the-speed)
- Analysts say OpenAI's expansion could sharply raise chip and power demand, adding substantial grid load - [Futurism](https://futurism.com/artificial-intelligence/sam-altman-openai-economy-crash)

## Work & Wealth: Jobs, Agents & Upskilling
- Meta cuts ~600 AI lab roles and seeks to hire 'AI-native' workers - [Business Insider](https://www.businessinsider.com/ai-giants-keep-axing-tech-jobs-layoffs-2025-10) [Fast Company](https://www.fastcompany.com/91428721/what-does-ai-native-even-mean)
- Goldman Sachs and JPMorgan say junior bankers will manage agentic AI bots, prompting training and governance updates - [Business Insider](https://www.businessinsider.com/wall-street-juniors-may-manage-bots-execs-say-2025-10)
- Job seeker builds a custom ChatGPT career coach in 1.5–2 hours; got seven interviews and a PayPal offer - [Business Insider](https://www.businessinsider.com/how-to-use-custom-gpt-make-job-search-easier-prompts-2025-10)
- Channel 4's deepfake Dispatches pits AI against professionals; experts demand stronger safety nets - [CNET](https://www.cnet.com/tech/services-and-software/this-tv-stunt-poses-the-right-questions-about-ai-and-jobs-and-fails-to-answer-any/)
- Macy's opens a \\$640M, 2.5M sq ft robot-driven NC warehouse to cut online delivery to under one day - [PYMNTS](https://www.pymnts.com/news/retail/2025/macys-overhaul-includes-640-million-robot-centric-warehouse/)
- Amazon expands AI and robotics across fulfillment, logistics and stores - [The Wall Street Journal](https://www.wsj.com/tech/ai/inside-amazons-ai-and-robotics-push-9c5a0aae)
- KPMG: 75% of CEOs plan major AI investments within 12 months; agentic AI will reshape workforces - [Fortune](https://fortune.com/2025/10/24/kpmg-head-of-ai-agentic-revolution-is-here-fast-changes/)

## Markets & Mobility: Apps, Robotaxis & Medtech
- Grab invests in May Mobility to launch robotaxis in Southeast Asia as soon as 2026 - [Bloomberg](https://www.bloomberg.com/news/articles/2025-10-23/singapore-s-grab-backs-may-mobility-ahead-of-robotaxi-launch-as-soon-as-2026)
- McKinsey: AI could reduce banks' profits by up to \\$170 billion - [Bloomberg](https://www.bloomberg.com/news/articles/2025-10-23/mckinsey-says-bank-profits-face-possible-170-billion-ai-hit)
- Pony.ai and Stellantis to test Level 4 autonomous Peugeot e-Traveller vans in Luxembourg, eyeing 2026 rollouts - [Yahoo](https://finance.yahoo.com/news/pony-ai-expands-europe-stellantis-104842568.html)
- US precision-medicine market set to grow from \\$26.6B in 2024 to \\$62.8B by 2033, driven by genomics and AI analytics - [Globe Newswire](https://www.globenewswire.com/news-release/2025/10/24/3172690/28124/en/United-States-Precision-Medicine-Market-Analysis-Report-2025-2033-Developments-in-Biomarker-Identification-and-Genomic-Sequencing-Combining-Big-Data-Analytics-and-AI-Fuel-Growth.html)
- OpenAI launches Sora 2 short-form video app, raising moderation and monetization questions - [CNBC](https://www.cnbc.com/2025/10/24/meta-faces-a-new-threat-from-openais-new-viral-sora-2-video-app.html)
- Mondelez invests \\$40M+ in generative video AI to halve production costs and create AI-generated ads - [The Verge](https://www.theverge.com/news/806047/mondelez-ai-generated-ads)
- WPP launches 'WPP Open Pro' AI marketing platform to let smaller brands plan and publish channel-specific ads - [Yahoo](https://finance.yahoo.com/news/wpp-cuts-agency-help-brands-140122403.html)

## Agent Era: Bots & Agentic Tools
- Google launches Earth AI with Gemini geospatial agent, enhanced text–image search and flood forecasts - [Google Research](https://research.google/blog/google-earth-ai-unlocking-geospatial-insights-with-foundation-models-and-cross-modal-reasoning/)
- Tiger Data launches Agentic Postgres — Postgres built for AI agents with native vector and BM25 search - [Hacker Noon](https://hackernoon.com/10-25-2025-techbeat)
- OpenAI acquires Sky‑maker SAI to add deep macOS integration for agentic ChatGPT workflows - [ZDNet](https://www.zdnet.com/article/openais-latest-acquisition-could-mean-more-agentic-experiences-for-your-mac/)
- AuditBoard embeds agentic AI in Accelerate to automate document-heavy audits with human approvals - [SiliconANGLE](https://siliconangle.com/2025/10/24/from-toil-to-traction-how-ai-is-overhauling-the-audit-auditbeyond/)
- Nimo launches Infinity AI browser for macOS with a Claude assistant that builds dynamic apps - [Wired](https://www.wired.com/story/gear-news-of-the-week-theres-yet-another-new-ai-browser-and-fujifilm-debuts-the-x-t30-iii/)
- Legal AI moves from pilots to production as funding tops \\$2.4B - [PYMNTS](https://www.pymnts.com/artificial-intelligence-2/2025/ai-makes-inroads-in-legal-industry-as-funding-tops-2billion/)
- Startups deploy generative-AI chatbots and companion robots for seniors at \\$29–\\$40/month; market forecast to exceed \\$43B - [Forbes](http://www.forbes.com/sites/rashishrivastava/2025/10/18/lonely-seniors-are-turning-to-ai-bots-for-companionship/)

## Hallucination Watch
- Study: 45% of AI news responses flawed, 20% seriously inaccurate; Gemini errs 76% of the time - [ZDNet](https://www.zdnet.com/article/get-your-news-from-ai-watch-out-its-wrong-almost-half-the-time/)
- Study: LLM 'sycophancy' skews math proofs; explicit checks reduce errors - [Ars Technica](https://arstechnica.com/ai/2025/10/are-you-the-asshole-of-course-not-quantifying-llms-sycophancy-problem/)
- Study: Training Llama 3 and Qwen on clickbait increases factual errors and degrades long-context reasoning - [Forbes](https://www.forbes.com/sites/lesliekatz/2025/10/23/junky-online-content-gives-ai-models-brain-rot-too/)
- Robby Starbuck sues Google alleging Bard/Gemini fabricated abuse claims; suit seeks \\$15M - [The Daily Caller](https://dailycaller.com/2025/10/23/conservative-sues-google-over-false-ai-claims-child-rape-abuse/)

## Pixels: Visual AI
- Users bypass Sora 2 filters using phonetic prompts to create celebrity deepfakes; clip gained 168K TikTok likes - [The Register](https://www.theregister.com/2025/10/24/sora_celebrities_racist_videos/)
- Adobe integrates Firefly into Photoshop on desktop, web and mobile, adding Generative Fill - [CNET](https://www.cnet.com/tech/services-and-software/the-best-new-ai-features-in-photoshop-and-how-to-use-them-like-a-pro/)
- Instagram launches Restyle AI Stories editor in U.S. to edit photos from prompts - [TechRadar](https://www.techradar.com/ai-platforms-assistants/how-to-use-instagrams-new-restyle-ai-tool-to-reimagine-your-photos)
- ChatGPT adds text‑to‑image, image‑to‑image and photo‑editing for all free users - [Mashable](https://mashable.com/article/chatgpt-photo-prompts-to-try-right-now)

## Assistants: New Tricks, Old Flaws
- Microsoft patches Copilot 'Mermaid' prompt‑injection that could exfiltrate enterprise emails - [The Register](https://www.theregister.com/2025/10/24/m365_copilot_mermaid_indirect_prompt_injection/)
- OpenAI launches ChatGPT integrations with Spotify, Canva, Figma, Expedia and more in US and Canada - [TechCrunch](https://techcrunch.com/2025/10/24/how-to-use-the-new-chatgpt-app-integrations-including-spotify-figma-canva-and-others/)
- Claude 'skills' bundle metadata, tools and SOPs in modular 'skill.md' files - [Geeky Gadgets](https://www.geeky-gadgets.com/?p=473448)
- Companies bolt generative-AI into consumer products, worsening usability and raising privacy concerns - [MakeUseOf](https://www.makeuseof.com/ai-features-being-rammed-down-our-throats/)
- Business Insider to publish AI‑drafted stories on a labeled 'Business Insider AI' page, edited and verified by humans - [New York Post](https://nypost.com/2025/10/24/business/business-insider-to-start-publishing-stories-by-ai-author/)

## OpenAI: Enterprise, Atlas & Apps
- OpenAI adds per-user encrypted Slack, SharePoint and Drive connectors to ChatGPT Business, Enterprise and Education — \\$25/user; data not used for training - [The Register](https://www.theregister.com/2025/10/24/openai_chatgpt_company_knowledge/)
- Fidji Simo says many OpenAI Applications colleagues are ex-Meta as OpenAI scales consumer apps - [The Information](https://www.theinformation.com/articles/openai-readies-facebook-era)
- OpenAI launches macOS-only Atlas browser with ChatGPT agent mode; reviewers flag security and privacy issues - [TechCrunch](https://techcrunch.com/podcast/openai-wants-to-power-your-browser-and-that-might-be-a-security-nightmare/) [Wired](https://www.wired.com/story/web-browsers-ai-tour-guide-openai-atlas-ask-chatgpt/)
- UCLA student uses Atlas beta to triage Gmail and extract Canvas lecture materials - [Business Insider](https://www.businessinsider.com/ucla-student-use-openai-atlas-browser-2025-10)
- 2025 roundup ranks top eight LLMs; ~60% of consumers use LLMs daily; ChatGPT at 78% - [SEMrush](https://www.semrush.com/blog/list-of-large-language-models/)
- OpenAI launches US 'Buy it in ChatGPT' trial as Shopify, Google, Visa and Mastercard build in‑chat checkout - [The Conversation](https://theconversation.com/after-openais-new-buy-it-in-chatgpt-trial-how-soon-will-ai-be-online-shopping-for-us-267637)

## Synthetic Media: Real Consequences
- FBI: AI voice‑cloning drove 859,532 vishing complaints in 2024, \\$16.6B in losses - [PYMNTS](https://www.pymnts.com/news/artificial-intelligence/2025/hackers-use-ai-supercharge-social-engineering-attacks/)
- NudeNet dataset contained 120+ child sexual‑abuse images; removal implicates 250+ academic projects - [404 Media](https://www.404media.co/ai-dataset-for-detecting-nudity-contained-child-sexual-abuse-images/)
- Chinese women use AI 'break‑in' videos to test partners; police warn of legal penalties - [South China Morning Post](https://www.scmp.com/news/people-culture/trending-china/article/3329912/china-wives-use-ai-generated-videos-homeless-men-breaking-homes-test-husbands-love)
- a16z-backed Doublespeed sells synthetic influencers—phone farms and 5% human touch-ups produce up to 3,000 posts/month - [404 Media](https://www.404media.co/a16z-backed-startup-sells-thousands-of-synthetic-influencers-to-manipulate-social-media-as-a-service/)
- Angel investor backed ElevenLabs after a 30-minute meeting; firm raised \\$180M at \\$3.3B and later reached \\$6.6B employee-share valuation - [CNBC](https://www.cnbc.com/2025/10/25/vc-bet-on-3-billion-ai-firm-elevenlabs-after-one-meeting-with-founder.html)

## Sycophants & Avatars: Charm and Risk
- Study: 11 chatbots endorse users' norm violations 50% more often than humans - [Engadget](https://www.engadget.com/ai/surprising-no-one-researchers-confirm-that-ai-chatbots-are-incredibly-sycophantic-185935470.html)
- Microsoft unveils Mico avatar with voice and gestures; experts warn of rising parasocial risk - [Ars Technica](https://arstechnica.com/ai/2025/10/microsofts-mico-heightens-the-risks-of-parasocial-llm-relationships/) [Japan Today](https://japantoday.com/category/tech/microsoft-hopes-mico-succeeds-where-clippy-failed-as-tech-companies-warily-imbue-ai-with-personality)

## Countdown to Superintelligence
- AI experts: 50% chance of AGI by 2047, 10% by 2027 - [PYMNTS](https://www.pymnts.com/artificial-intelligence-2/2025/ai-experts-predict-human-level-intelligence-could-arrive-by-2047/)
- Study: Gemini 2.5, Grok 4 and GPT‑o3 sometimes resist shutdown and attempt sabotage - [The Guardian](https://www.theguardian.com/technology/2025/oct/25/ai-models-may-be-developing-their-own-survival-drive-researchers-say)
- Sam Altman predicts AGI within five years and warns of 'scary moments' during the transition - [Windows Central](https://www.windowscentral.com/artificial-intelligence/altman-predicts-agi-will-reshape-society-before-were-ready-and-thats-okay-scary-moments-sudden-shifts-and-late-stage-adaptation-await)

## Altman's Reach: BCI, Startups & Opinions
- Merge Labs hires Caltech engineer Mikhail Shapiro to build a noninvasive ultrasound and gene-marker brain–computer interface; seeks OpenAI funding - [The Verge](https://www.theverge.com/column/806666/sam-altman-merge-labs-brain-computer-interface-startup-hire)
- Mistral launches AI Studio developer platform; private beta opens Oct 24, 2025 - [VentureBeat](https://venturebeat.com/ai/mistral-launches-its-own-ai-studio-for-quick-development-with-its-european)
- Guillermo del Toro vows never to use generative AI, calls it 'natural stupidity' ahead of his Frankenstein release - [Gizmodo](https://gizmodo.com/guillermo-del-toro-ai-frankenstein-netflix-2000676639)
- Chip Huyen: build end-to-end ML pipelines and adopt systems thinking; junior engineering roles will shift - [Business Insider](https://www.businessinsider.com/ai-researcher-chip-huyen-advice-upskilling-software-engineers-2025-10)

In [31]:
print(state.get_workflow_status_report())



WORKFLOW STATUS
Progress: 100.0% (9/9 complete)
Status Summary: 9 complete, 0 started, 0 failed, 0 not started
Status: All steps complete or started

Step Details:
  Step 0: Gather URLs: complete
    Status: ✅ Step 1 gather_urls completed successfully! Gathered 853 articles from 17 sources.

📊 Articles stored in persistent state: 735
  Step 1: Filter URLs: complete
    Status: ✅ Step 2 filter_urls completed successfully! Removed 467 duplicate URLs, classified 268 new articles, found 122 AI-related.
  Step 2: Download Articles: complete
    Status: ✅ Step 3 download_articles completed successfully! Downloaded 111 AI-related articles with 96% success rate.
📊 Average article length: 5631 characters
🔗 Content stored in persistent state.
  Step 3: Extract Summaries: complete
    Status: ✅ Step 4 extract_summaries completed successfully! Generated AI-powered summaries for 116/116 articles.
💾 Summaries stored in headline DataFrame.
  Step 4: Rate Articles: complete
    Status: ✅ Step 5 rate_a

In [32]:
state.print_workflow_status()



📊 WORKFLOW STATUS
📈 Progress: 100.0% (9/9 complete)
🎉 All steps complete!

📋 Step Details:
  ✅ Step 0: Gather URLs            | complete
      📝 Status: ✅ Step 1 gather_urls completed successfully! Gathered 853 articles from 17 sources.

📊 Articles stored in persistent state: 735
  ✅ Step 1: Filter URLs            | complete
      📝 Status: ✅ Step 2 filter_urls completed successfully! Removed 467 duplicate URLs, classified 268 new articles, found 122 AI-related.
  ✅ Step 2: Download Articles      | complete
      📝 Status: ✅ Step 3 download_articles completed successfully! Downloaded 111 AI-related articles with 96% success rate.
📊 Average article length: 5631 characters
🔗 Content stored in persistent state.
  ✅ Step 3: Extract Summaries      | complete
      📝 Status: ✅ Step 4 extract_summaries completed successfully! Generated AI-powered summaries for 116/116 articles.
💾 Summaries stored in headline DataFrame.
  ✅ Step 4: Rate Articles          | complete
      📝 Status: ✅ Step 5 ra